In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import numpy as np
import pandas as pd
import torch
import re
from sklearn.metrics import balanced_accuracy_score, roc_auc_score,accuracy_score,precision_recall_fscore_support
from Constants import *
from Preprocessing import *
from Models import *
import copy
from Utils import *
pd.set_option('display.max_rows', 200)



In [3]:
pd.read_csv('../data/digital_twin_ln_monograms.csv')

id  L1A  L1B  L2A  L2B   L3   L4  L5A  L5B   L6  ...  R1A  R1B  R2A  \
0        3  0.0  0.0  1.0  1.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   
1        5  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  1.0   
2        6  0.0  0.0  1.0  1.0  1.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  1.0   
3        7  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   
4        8  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  1.0   
..     ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
531  10201  0.0  0.0  1.0  1.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   
532  10202  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  1.0   
533  10203  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  1.0   
534  10204  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  1.0   
535  10205  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   

     R2B   R3   R4  R5A  R5B   R6  RRPLN  
0    0.0  0.0  0.0  0.0  0.0  0.0    0.0  
1    1.0  0.0  0.0  0.0  0.0  0.0    0.0  
2    1.0  1.0  0.0  0.0  0.0  0.0    0.0  
3    0.0  0.0  0.0  0.0  0.0  0.0    0.0  
4    1.0  0.0  0.0  0.0  0.0  0.0    0.0  
..   ...  ...  ...  ...  ...  ...    ...  
531  0.0  0.0  0.0  0.0  0.0  0.0    0.0  
532  1.0  0.0  0.0  0.0  0.0  0.0    0.0  
533  1.0  1.0  0.0  0.0  0.0  0.0    0.0  
534  1.0  1.0  0.0  0.0  0.0  0.0    0.0  
535  0.0  1.0  0.0  0.0  0.0  0.0    0.0  

[536 rows x 21 columns]

In [4]:
data = DTDataset(use_smote=True)
data.processed_df.T
# data.processed_df#.shape, len(data.processed_df.index.unique())

/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


id                                    3      5          6          7      \
hpv                                       1      0          1          1   
age                               55.969444  20.95  69.930556  72.319444   
packs_per_year                          0.0   38.0       35.0        0.0   
gender                                    1      1          0          1   
smoking_status                          0.0    1.0        1.0        1.0   
Aspiration rate Pre-therapy               0      0          1          0   
total_dose                             66.0   72.0       70.0       70.0   
dose_fraction                           2.2    1.8   2.121212   2.121212   
bilateral                             False  False       True      False   
White/Caucasion                        True   True       True       True   
Hispanic/Latino                       False  False      False      False   
African American/Black                False  False      False      False   
Asian                                 False  False      False      False   
cc_none                                   0      0          0          1   
cc_platinum                               0      1          1          0   
cc_cetuximab                              1      0          0          0   
cc_others                                 0      0          0          0   
no_dose_adjustment                        1      1          1          1   
dose_modified                             0      0          0          0   
dose_delayed                              0      0          0          0   
dose_cancelled                            0      0          0          0   
dose_delayed_&_modified                   0      0          0          0   
regiment_modification                     0      0          0          0   
unknown                                   0      0          0          0   
T-category_1                              0      0          0          1   
T-category_2                              1      0          0          0   
T-category_3                              0      0          0          0   
T-category_4                              0      1          1          0   
N-category_0                              0      0          0          0   
N-category_1                              1      0          0          0   
N-category_2                              0      1          1          1   
N-category_3                              0      0          0          0   
AJCC_1                                    1      0          0          0   
AJCC_2                                    0      0          0          1   
AJCC_3                                    0      0          1          0   
AJCC_4                                    0      1          0          0   
Pathological Grade_0                      1      0          0          1   
Pathological Grade_1                      0      0          0          0   
Pathological Grade_2                      0      1          1          0   
Pathological Grade_3                      0      0          0          0   
Pathological Grade_4                      0      0          0          0   
subsite_BOT                               1      1          1          0   
subsite_GPS                               0      0          0          0   
subsite_NOS                               0      0          0          1   
subsite_Soft palate                       0      0          0          0   
subsite_Tonsil                            0      0          0          0   
treatment_CC                              1      1          1          0   
treatment_IC+CC                           0      0          0          0   
treatment_IC+Radiation alone              0      0          0          0   
treatment_Radiation alone                 0      0          0          1   
DLT_Dermatological                      0.0    0.0        0.0        0.0   
DLT_Neurological                        0.0    0

In [5]:
get_tt_split()[1]

[133,
 47,
 35,
 10,
 279,
 5056,
 5035,
 224,
 209,
 10063,
 2006,
 5020,
 271,
 10014,
 5080,
 10097,
 10125,
 10106,
 2032,
 10169,
 2024,
 286,
 2015,
 2019,
 10026,
 5040,
 236,
 187,
 10161,
 211,
 5103,
 10178,
 2026,
 10137,
 184,
 199,
 10040,
 272,
 68,
 5105,
 10177,
 228,
 44,
 242,
 9,
 5101,
 10104,
 10165,
 10007,
 10133,
 10145,
 10016,
 264,
 5098,
 10023,
 10050,
 5120,
 227,
 5118,
 2005,
 5053,
 10135,
 5007,
 10092,
 36,
 2001,
 5115,
 10005,
 10102,
 189,
 5036,
 10088,
 254,
 10130,
 10086,
 25,
 5001,
 5065,
 10084,
 195,
 5099,
 3,
 5093,
 10094,
 7,
 5038,
 10068,
 5032,
 202,
 274,
 45,
 2017,
 10176,
 217,
 10160,
 5082,
 10012,
 10017,
 10100,
 2031,
 77,
 10066,
 5078,
 117,
 10010,
 10170,
 10190,
 10058,
 5049,
 5086,
 5052,
 268,
 2029,
 5084,
 10105,
 10013,
 245,
 5048,
 2020,
 215,
 10046,
 5117,
 5033,
 267,
 5003,
 168,
 31,
 10049,
 10180,
 190,
 287,
 284,
 5054,
 10101,
 208,
 5077,
 10091,
 10172,
 288,
 5109,
 10126,
 10153,
 10123,
 5107,
 19

In [6]:
get_tt_split(resample_training=True)[0]

array([ 2023,    57, 10095,  5018,    18, 10003,   239, 10163,  5044,
        5075,  5100,   269, 10061, 10152, 10147,   218, 10163,    74,
       10082, 10164, 10114,  5104, 10025,  5023,  5058, 10132,   230,
       10073, 10015,  5100,   103,  5059,   282,  2028,  5030, 10074,
        2030,  5051,    64,  5021, 10164,    87, 10078,   256,    94,
        2027,   216,    38,    94, 10074,    40,   239,   289,   269,
        5069,    51,   252,  5074, 10045,    15, 10205,   237,  2033,
         280, 10117,  5021,  5072, 10109,     6, 10183,  5113, 10109,
       10083, 10195, 10078, 10043,   178,   241, 10138,  5031,    56,
        5005, 10022,  5074,    94,   200,   200, 10197,   213, 10148,
       10162,   206,  5014,   229, 10134, 10079,    32,    53,   257,
         231,   289,   249,  2022,   257, 10024,   210, 10081, 10071,
        2003, 10199,  2013,   229, 10195,  2011,  5055,   205,  5097,
       10111,    26, 10052, 10204,  2028, 10022,  5112, 10158, 10129,
       10197,    27,

In [33]:
def nllloss(ytrue,ypred):
    #nll loss with argmax added in
    loss = torch.nn.NLLLoss()
    return loss(ypred,ytrue.argmax(axis=1))

def state_loss(ytrue,ypred,weights=None):
    if weights is None:
        weights = [1,1,1,1]
    pd_loss = torch.mul(nllloss(ytrue[0],ypred[0]),weights[0])
    nd_loss = torch.mul(nllloss(ytrue[1],ypred[1]),weights[1])
    mod_loss = torch.mul(nllloss(ytrue[2],ypred[2]),weights[2])
    loss = torch.add(pd_loss,torch.add(nd_loss,mod_loss))
    dlt_true = ytrue[3]
    dlt_pred = ypred[3]
    ndlt = dlt_true.shape[1]
#     nloss = torch.nn.NLLLoss()
    bce = torch.nn.BCELoss()
    for i in range(ndlt):
        dlt_loss = bce(dlt_pred[:,i].view(-1),dlt_true[:,i].view(-1))
        dlt_loss = torch.mul(dlt_loss,weights[3]/ndlt)
        loss = torch.add(loss,dlt_loss)
    return loss

def outcome_loss(ytrue,ypred,weights=None):
    if weights is None:
        weights = [1,1,1,1]
    loss = 0
    nloss = torch.nn.BCELoss()
    for i in range(len(weights)):
        iloss = nloss(ypred[:,i],ytrue[i])*weights[i]
        loss += iloss
    return loss

def mc_metrics(yt,yp,numpy=False,is_dlt=False):
    if not numpy:
        yt = yt.cpu().detach().numpy()
        yp = yp.cpu().detach().numpy()
    #dlt prediction (binary)
    if is_dlt:
        acc = accuracy_score(yt,yp>.5)
        if yt.sum() > 1:
            try:
                auc = roc_auc_score(yt,yp)
            except:
                auc = -1
        else:
            auc=-1
        error = np.mean((yt-yp)**2)
        return {'accuracy': acc, 'mse': error, 'auc': auc}
    #this is a catch for when I se the dlt prediction format (encoded integer ordinal, predict as a categorical and take the argmax)
    elif yt.ndim > 1:
        try:
            bacc = balanced_accuracy_score(yt.argmax(axis=1),yp.argmax(axis=1))
        except:
            bacc = -1
        try:
            roc_micro = roc_auc_score(yt,yp,average='micro')
        except:
            roc_micro=-1
        try:
            roc_macro = roc_auc_score(yt,yp,average='macro')
        except Exception as e:
            try: 
                roc_macro = roc_auc_score(yt[:,0:2],yp[:,0:2],average='macro')
            except:
                roc_macro = -1
        try:
            roc_weighted = roc_auc_score(yt,yp,average='weighted')
        except:
            try:
                roc_weighted = roc_auc_score(yt[:,0:2],yp[:,0:2],average='weighted')
            except:
                roc_weighted= -1
        return {'accuracy': bacc, 'auc_micro': roc_micro,'auc_mean': roc_macro,'auc_weighted': roc_weighted}
    #outcomes (binary)
    else:
        multiclass = yp.ndim > 1
        if multiclass:
            yp = yp.argmax(axis=1)
        try:
            if not multiclass:
                bacc = accuracy_score(yt,(yp>.5).astype(int))
            else:
                bacc = accuracy_score(yt,yp)
        except Exception as e:
            print(e,yp,yt)
            bacc = -1
        try:
            roc = roc_auc_score(yt,yp)
        except:
            roc = -1
        try:
            if not multiclass:
                pr,re,fscore,supp = precision_recall_fscore_support(yt,(yp>.5).astype(int),average='binary')
            else:
                pr,re,fscore,supp = precision_recall_fscore_support(yt,yp,average='macro')
        except Exception as e:
            print(e)
            [pr,re,fscore,supp] = [-1,-1,-1,-1]
        error = np.mean((yt-yp)**2)
        return {'accuracy': bacc, 'mse': error, 'auc': roc,'precision': pr,'recall':re,'f1':fscore}

def state_metrics(ytrue,ypred,numpy=False):
    pd_metrics = mc_metrics(ytrue[0],ypred[0],numpy=numpy)
    nd_metrics = mc_metrics(ytrue[1],ypred[1],numpy=numpy)
    mod_metrics = mc_metrics(ytrue[1],ypred[1],numpy=numpy)
    
    dlt_metrics = []
    dlt_true = ytrue[3]
    dlt_pred = ypred[3]
    ndlt = dlt_true.shape[1]
    nloss = torch.nn.NLLLoss()
    for i in range(ndlt):
        dm = mc_metrics(dlt_true[:,i],dlt_pred[:,i].view(-1),is_dlt=True)
        dlt_metrics.append(dm)
    dlt_acc =[d['accuracy'] for d in dlt_metrics]
    dlt_error = [d['mse'] for d in dlt_metrics]
    dlt_auc = [d['auc'] for d in dlt_metrics]
    
    acc_mean = np.mean([a for a in dlt_acc if a >= 0 and a < 1])
    auc_mean = np.mean([a for a in dlt_auc if a >= 0])
    results = {'pd': pd_metrics,'nd': nd_metrics,'mod': mod_metrics,
               'dlts': {'accuracy': dlt_acc,'accuracy_mean': acc_mean,'auc': dlt_auc,'auc_mean': auc_mean}
              }
    return results

def outcome_metrics(ytrue,ypred,numpy=False):
    res = {}
    for i, outcome in enumerate(Const.outcomes):
        metrics = mc_metrics(ytrue[i],ypred[:,i])
        res[outcome] = metrics
    return res

def transition_sample(state):
    ids = get_dt_ids()
    
    train_ids, test_ids = get_tt_split()
    
    dataset = DTDataset()
    
    #only train on people with  IC for state 1 since other people can't have any outcomes otherwise
    require = None
    if state == 1:
        require = Const.decisions[0] #we don't expect a state update if there is no treatment
        valid_ids = dataset.get_input_state(require=require).index.values
        train_ids = [t for t in train_ids if t in valid_ids]
        test_ids = [t for t in test_ids if t in valid_ids]
    xtrain = dataset.get_input_state(step=state,ids=train_ids,require=require)
    xtest = dataset.get_input_state(step=state,ids=test_ids,require=require)
    ytrain = dataset.get_intermediate_outcomes(step=state,ids=train_ids,require=require)
    ytest = dataset.get_intermediate_outcomes(step=state,ids=test_ids,require=require)

    xtrain = df_to_torch(xtrain)
    xtest = df_to_torch(xtest)
    ytrain = [df_to_torch(t) for t in ytrain]
    ytest= [df_to_torch(t) for t in ytest]
    return xtrain,xtest,ytrain,ytest

In [105]:
def train_state(model=None,
                model_args={},
                state=1,
                split=.7,
                lr=.001,
                epochs=1000,
                patience=10,
                use_attention=False,
                weights=None,
                save_path='../data/models/',
                use_default_split=True,
                use_bagging_split=False,
                resample_training=False,#use bootstraping on training data after splitting
                n_validation_trainsteps=2,
                verbose=True,
                use_smote=True,
                file_suffix=''):
    
    ids = get_dt_ids()
    
    train_ids, test_ids = get_tt_split(use_default_split=use_default_split,use_bagging_split=use_bagging_split,resample_training=resample_training)

    if use_smote:
        dataset = DTDataset(use_smote=True,smote_ids = train_ids,smote_columns=[Const.decisions[state-1]])
        train_ids = [i for i in dataset.processed_df.index.values if i not in test_ids]
    else:
        dataset = DTDataset()
    
    #only train on people with  IC for state 1 since other people can't have any outcomes otherwise
    require = None
    if state == 1:
        require = Const.decisions[0] #we don't expect a state update if there is no treatment
        valid_ids = dataset.get_input_state(require=require).index.values
        train_ids = [t for t in train_ids if t in valid_ids]
        test_ids = [t for t in test_ids if t in valid_ids]
    xtrain = dataset.get_input_state(step=state,ids=train_ids,require=require)
    xtest = dataset.get_input_state(step=state,ids=test_ids,require=require)
    ytrain = dataset.get_intermediate_outcomes(step=state,ids=train_ids,require=require)
    ytest = dataset.get_intermediate_outcomes(step=state,ids=test_ids,require=require)
    

    if not use_attention:
        model_args = {k:v for k,v in model_args.items() if 'attention' not in k and 'embed_size' not in k}
    if state < 3:
        if model is None:
            if use_attention:
                model = OutcomeAttentionSimulator(xtrain.shape[1],state=state,**model_args)
            else:
                model = OutcomeSimulator(xtrain.shape[1],state=state,**model_args)
        lfunc = state_loss
        if weights is None:
            weights = [1,1,.1,1]
    else:
        if model is None:
            if use_attention:
                model = EndpointAttentionSimulator(xtrain.shape[1],**model_args)
            else:
                model = EndpointSimulator(xtrain.shape[1],**model_args)
        if weights is None:
            weights = [1,1,1,1]
        lfunc = outcome_loss
        
    device = 'cuda' if torch.cuda.is_available() else 'cpu'
    model.set_device(device)
    
    hashcode = str(hash(','.join([str(i) for i in train_ids])))
    save_file = save_path + 'model_' + model.identifier + '_split' + str(split) + '_resample' + str(resample_training) +  '_hash' + hashcode + file_suffix + '.tar'
    xtrain = df_to_torch(xtrain).to(device)
    if use_attention:
        model.save_memory(xtrain)
    xtest = df_to_torch(xtest).to(device)
    ytrain = [df_to_torch(t).to(device) for t in ytrain]
    ytest= [df_to_torch(t).to(device) for t in ytest]
    
    model.fit_normalizer(xtrain)
#     normalize = lambda x: (x - xtrain.mean(axis=0)+.01)/(xtrain.std(axis=0)+.01)
#     unnormalize = lambda x: (x * (xtrain.std(axis=0) +.01)) + xtrain.mean(axis=0) - .01
    
    optimizer = torch.optim.Adam(model.parameters(),lr=lr)
    best_val_loss = 1000000000000000000000000000
    best_loss_metrics = {}
    last_epoch = False
    for epoch in range(epochs):
        
        model.train(True)
        optimizer.zero_grad()
        
        xtrain_sample = xtrain#[torch.randint(len(xtrain),(len(xtrain),) )]
        ypred = model(xtrain_sample)
        loss = lfunc(ytrain,ypred,weights=weights)

        loss.backward()
        optimizer.step()
        if verbose:
            print('epoch',epoch,'train loss',loss.item())
        
        model.eval()
        if use_attention:
            yval = model(xtest,use_saved_memory=True)
        else:
            yval = model(xtest)
        val_loss = lfunc(ytest,yval,weights=weights)
        if state < 3:
            val_metrics = state_metrics(ytest,yval)
        else:
            val_metrics = outcome_metrics(ytest,yval)
        if val_loss.item() < best_val_loss:
            best_val_loss = val_loss.item()
            best_loss_metrics = val_metrics
            steps_since_improvement = 0
            torch.save(model.state_dict(),save_file)
        else:
            steps_since_improvement += 1
        if verbose:
            print('val loss',val_loss.item())
            print('______________')
        if steps_since_improvement > patience:
            break
    print('best loss',best_val_loss,best_loss_metrics)
    model.load_state_dict(torch.load(save_file))
    
    #train one step on validation data
    for i in range(n_validation_trainsteps):
        model.train()
        yval = model(xtest)
        val_loss = lfunc(ytest,yval,weights=weights)
        val_loss.backward()
        optimizer.step()
        torch.save(model.state_dict(),save_file)
    
    model.eval()
    return model,  best_val_loss, best_loss_metrics

t1_args = {'hidden_layers': [100],
   'dropout': 0.1,
   'input_dropout': 0.1}
train_state(model_args=t1_args,lr=.0001,weights=[1,1,.1,.1],use_attention=False)

here
epoch 0 train loss 2.456239700317383


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


val loss 2.4510746002197266
______________
epoch 1 train loss 2.4563913345336914
val loss 2.4480161666870117
______________
epoch 2 train loss 2.4474682807922363
val loss 2.4449756145477295
______________
epoch 3 train loss 2.443561315536499
val loss 2.4419350624084473
______________
epoch 4 train loss 2.445147752761841
val loss 2.438905954360962
______________
epoch 5 train loss 2.444157361984253
val loss 2.435896158218384
______________
epoch 6 train loss 2.4357430934906006
val loss 2.4328958988189697
______________
epoch 7 train loss 2.43440842628479
val loss 2.4299063682556152
______________
epoch 8 train loss 2.43412709236145
val loss 2.4269187450408936
______________
epoch 9 train loss 2.426119804382324
val loss 2.4239344596862793
______________
epoch 10 train loss 2.4225966930389404
val loss 2.4209601879119873
______________
epoch 11 train loss 2.41686749458313
val loss 2.4179959297180176
______________
epoch 12 train loss 2.4141438007354736
val loss 2.4150431156158447
_________

val loss 2.1767613887786865
______________
epoch 103 train loss 2.144089937210083
val loss 2.174314022064209
______________
epoch 104 train loss 2.138460159301758
val loss 2.1718738079071045
______________
epoch 105 train loss 2.138489246368408
val loss 2.1694369316101074
______________
epoch 106 train loss 2.13389253616333
val loss 2.1670055389404297
______________
epoch 107 train loss 2.126570701599121
val loss 2.1645774841308594
______________
epoch 108 train loss 2.123467206954956
val loss 2.1621510982513428
______________
epoch 109 train loss 2.1208739280700684
val loss 2.1597249507904053
______________
epoch 110 train loss 2.1157445907592773
val loss 2.1572988033294678
______________
epoch 111 train loss 2.1102569103240967
val loss 2.1548783779144287
______________
epoch 112 train loss 2.1110332012176514
val loss 2.1524617671966553
______________
epoch 113 train loss 2.106163501739502
val loss 2.1500446796417236
______________
epoch 114 train loss 2.104628324508667
val loss 2.147

epoch 202 train loss 1.8554496765136719
val loss 1.953980803489685
______________
epoch 203 train loss 1.8521836996078491
val loss 1.9520454406738281
______________
epoch 204 train loss 1.8594894409179688
val loss 1.9501166343688965
______________
epoch 205 train loss 1.8498023748397827
val loss 1.948193073272705
______________
epoch 206 train loss 1.8393288850784302
val loss 1.9462767839431763
______________
epoch 207 train loss 1.8407078981399536
val loss 1.9443731307983398
______________
epoch 208 train loss 1.8410327434539795
val loss 1.9424632787704468
______________
epoch 209 train loss 1.8443225622177124
val loss 1.9405616521835327
______________
epoch 210 train loss 1.8295903205871582
val loss 1.938673496246338
______________
epoch 211 train loss 1.8275232315063477
val loss 1.9367982149124146
______________
epoch 212 train loss 1.8327604532241821
val loss 1.9349350929260254
______________
epoch 213 train loss 1.828269600868225
val loss 1.9330894947052002
______________
epoch 21

val loss 1.802121639251709
______________
epoch 303 train loss 1.606344223022461
val loss 1.8010526895523071
______________
epoch 304 train loss 1.603141188621521
val loss 1.7999849319458008
______________
epoch 305 train loss 1.6115716695785522
val loss 1.7989171743392944
______________
epoch 306 train loss 1.6052794456481934
val loss 1.7978585958480835
______________
epoch 307 train loss 1.5952422618865967
val loss 1.7968204021453857
______________
epoch 308 train loss 1.5944966077804565
val loss 1.795792818069458
______________
epoch 309 train loss 1.602068305015564
val loss 1.7947765588760376
______________
epoch 310 train loss 1.5843639373779297
val loss 1.793765902519226
______________
epoch 311 train loss 1.5860213041305542
val loss 1.792764663696289
______________
epoch 312 train loss 1.5765821933746338
val loss 1.7917808294296265
______________
epoch 313 train loss 1.567512035369873
val loss 1.790803074836731
______________
epoch 314 train loss 1.591080665588379
val loss 1.789

epoch 406 train loss 1.4129695892333984
val loss 1.7356956005096436
______________
epoch 407 train loss 1.4190670251846313
val loss 1.7354204654693604
______________
epoch 408 train loss 1.4005684852600098
val loss 1.7351425886154175
______________
epoch 409 train loss 1.4047553539276123
val loss 1.7348803281784058
______________
epoch 410 train loss 1.4250233173370361
val loss 1.7346274852752686
______________
epoch 411 train loss 1.412868618965149
val loss 1.7343922853469849
______________
epoch 412 train loss 1.413565754890442
val loss 1.734152913093567
______________
epoch 413 train loss 1.4208979606628418
val loss 1.7339175939559937
______________
epoch 414 train loss 1.4051403999328613
val loss 1.73369562625885
______________
epoch 415 train loss 1.4017237424850464
val loss 1.7334728240966797
______________
epoch 416 train loss 1.410704493522644
val loss 1.7332497835159302
______________
epoch 417 train loss 1.4011036157608032
val loss 1.733025074005127
______________
epoch 418 t

(OutcomeSimulator(
   (input_dropout): Dropout(p=0.1, inplace=False)
   (layers): ModuleList(
     (0): Linear(in_features=56, out_features=100, bias=True)
     (1): ReLU()
   )
   (batchnorm): BatchNorm1d(100, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
   (dropout): Dropout(p=0.1, inplace=False)
   (relu): Softplus(beta=1, threshold=20)
   (sigmoid): Sigmoid()
   (softmax): LogSoftmax(dim=1)
   (disease_layer): Linear(in_features=100, out_features=3, bias=True)
   (nodal_disease_layer): Linear(in_features=100, out_features=3, bias=True)
   (dlt_layers): ModuleList(
     (0-7): 8 x Linear(in_features=100, out_features=1, bias=True)
   )
   (treatment_layer): Linear(in_features=100, out_features=7, bias=True)
 ),
 1.7277640104293823,
 {'pd': {'accuracy': 0.4157142857142857,
   'auc_micro': 0.7715242346938775,
   'auc_mean': 0.546985473465822,
   'auc_weighted': 0.6260027166937624},
  'nd': {'accuracy': 0.3333333333333333,
   'auc_micro': 0.8427550357374918,
   'auc_

In [106]:
train_state(model_args=t1_args,lr=.0001,weights=[1,1,.1,.1],use_attention=False,use_smote=True)

here
epoch 0 train loss 2.4606335163116455
val loss 2.4513282775878906
______________
epoch 1 train loss 2.458585500717163


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


val loss 2.4487061500549316
______________
epoch 2 train loss 2.46178936958313
val loss 2.4460806846618652
______________
epoch 3 train loss 2.4601454734802246
val loss 2.4434642791748047
______________
epoch 4 train loss 2.4568779468536377
val loss 2.440854549407959
______________
epoch 5 train loss 2.450415849685669
val loss 2.4382500648498535
______________
epoch 6 train loss 2.447375535964966
val loss 2.4356515407562256
______________
epoch 7 train loss 2.44437313079834
val loss 2.4330620765686035
______________
epoch 8 train loss 2.4452531337738037
val loss 2.430478811264038
______________
epoch 9 train loss 2.4369289875030518
val loss 2.4279041290283203
______________
epoch 10 train loss 2.4371118545532227
val loss 2.42533802986145
______________
epoch 11 train loss 2.4315898418426514
val loss 2.4227752685546875
______________
epoch 12 train loss 2.427912950515747
val loss 2.4202213287353516
______________
epoch 13 train loss 2.4239330291748047
val loss 2.4176747798919678
_______

val loss 2.1987764835357666
______________
epoch 108 train loss 2.1668362617492676
val loss 2.196547031402588
______________
epoch 109 train loss 2.154524803161621
val loss 2.194317102432251
______________
epoch 110 train loss 2.1583380699157715
val loss 2.192091941833496
______________
epoch 111 train loss 2.1584014892578125
val loss 2.189868211746216
______________
epoch 112 train loss 2.155076503753662
val loss 2.1876466274261475
______________
epoch 113 train loss 2.145552396774292
val loss 2.185426950454712
______________
epoch 114 train loss 2.1525394916534424
val loss 2.1832056045532227
______________
epoch 115 train loss 2.145988702774048
val loss 2.1809871196746826
______________
epoch 116 train loss 2.14011287689209
val loss 2.178771734237671
______________
epoch 117 train loss 2.1400721073150635
val loss 2.176560163497925
______________
epoch 118 train loss 2.1311304569244385
val loss 2.174342155456543
______________
epoch 119 train loss 2.1375696659088135
val loss 2.1721255

epoch 211 train loss 1.8670235872268677
val loss 1.9760068655014038
______________
epoch 212 train loss 1.856703758239746
val loss 1.974064826965332
______________
epoch 213 train loss 1.8635201454162598
val loss 1.9721267223358154
______________
epoch 214 train loss 1.860953688621521
val loss 1.9701944589614868
______________
epoch 215 train loss 1.8579033613204956
val loss 1.9682844877243042
______________
epoch 216 train loss 1.8540617227554321
val loss 1.966387391090393
______________
epoch 217 train loss 1.8624097108840942
val loss 1.964499831199646
______________
epoch 218 train loss 1.8518155813217163
val loss 1.962610125541687
______________
epoch 219 train loss 1.8459566831588745
val loss 1.9607319831848145
______________
epoch 220 train loss 1.8389122486114502
val loss 1.9588642120361328
______________
epoch 221 train loss 1.83620023727417
val loss 1.9569978713989258
______________
epoch 222 train loss 1.835019826889038
val loss 1.9551379680633545
______________
epoch 223 tra

val loss 1.8195600509643555
______________
epoch 315 train loss 1.603292465209961
val loss 1.8185254335403442
______________
epoch 316 train loss 1.5919049978256226
val loss 1.8174959421157837
______________
epoch 317 train loss 1.5998153686523438
val loss 1.8164681196212769
______________
epoch 318 train loss 1.5945026874542236
val loss 1.8154594898223877
______________
epoch 319 train loss 1.5794650316238403
val loss 1.814458966255188
______________
epoch 320 train loss 1.5986440181732178
val loss 1.8134769201278687
______________
epoch 321 train loss 1.590964436531067
val loss 1.812517523765564
______________
epoch 322 train loss 1.5887776613235474
val loss 1.8115607500076294
______________
epoch 323 train loss 1.5777199268341064
val loss 1.810599684715271
______________
epoch 324 train loss 1.5762850046157837
val loss 1.8096407651901245
______________
epoch 325 train loss 1.5745556354522705
val loss 1.8086800575256348
______________
epoch 326 train loss 1.5728322267532349
val loss 

epoch 418 train loss 1.401861310005188
val loss 1.7602227926254272
______________
epoch 419 train loss 1.396628737449646
val loss 1.7600380182266235
______________
epoch 420 train loss 1.3957386016845703
val loss 1.7598686218261719
______________
epoch 421 train loss 1.3963472843170166
val loss 1.7597005367279053
______________
epoch 422 train loss 1.404457926750183
val loss 1.7595385313034058
______________
epoch 423 train loss 1.398054599761963
val loss 1.7593880891799927
______________
epoch 424 train loss 1.389243245124817
val loss 1.7592564821243286
______________
epoch 425 train loss 1.3880811929702759
val loss 1.7591356039047241
______________
epoch 426 train loss 1.3846182823181152
val loss 1.7590185403823853
______________
epoch 427 train loss 1.3860727548599243
val loss 1.7589062452316284
______________
epoch 428 train loss 1.3941782712936401
val loss 1.7587958574295044
______________
epoch 429 train loss 1.3932658433914185
val loss 1.7587027549743652
______________
epoch 430

(OutcomeSimulator(
   (input_dropout): Dropout(p=0.1, inplace=False)
   (layers): ModuleList(
     (0): Linear(in_features=56, out_features=100, bias=True)
     (1): ReLU()
   )
   (batchnorm): BatchNorm1d(100, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
   (dropout): Dropout(p=0.1, inplace=False)
   (relu): Softplus(beta=1, threshold=20)
   (sigmoid): Sigmoid()
   (softmax): LogSoftmax(dim=1)
   (disease_layer): Linear(in_features=100, out_features=3, bias=True)
   (nodal_disease_layer): Linear(in_features=100, out_features=3, bias=True)
   (dlt_layers): ModuleList(
     (0-7): 8 x Linear(in_features=100, out_features=1, bias=True)
   )
   (treatment_layer): Linear(in_features=100, out_features=7, bias=True)
 ),
 1.7582471370697021,
 {'pd': {'accuracy': 0.3742857142857143,
   'auc_micro': 0.7578125,
   'auc_mean': 0.5321963968617659,
   'auc_weighted': 0.6018603546064615},
  'nd': {'accuracy': 0.3333333333333333,
   'auc_micro': 0.8307342430149448,
   'auc_mean': 0

In [108]:
train_state(model_args=t1_args,state=2,lr=.001,weights=[1,1,.1,10],use_smote=False)

epoch 0 train loss 7.795362949371338
val loss 8.001863479614258
______________
epoch 1 train loss 7.680380344390869
val loss 7.864813327789307
______________
epoch 2 train loss 7.529154300689697
val loss 7.730773448944092
______________
epoch 3 train loss 7.372957706451416
val loss 7.598876953125
______________
epoch 4 train loss 7.25274133682251
val loss 7.46916389465332
______________
epoch 5 train loss 7.116682052612305
val loss 7.341419219970703
______________
epoch 6 train loss 6.975031852722168
val loss 7.215181350708008
______________
epoch 7 train loss 6.84866189956665
val loss 7.089906692504883
______________
epoch 8 train loss 6.735424995422363
val loss 6.965451240539551
______________
epoch 9 train loss 6.607348442077637
val loss 6.841794490814209
______________
epoch 10 train loss 6.47620964050293
val loss 6.718975067138672
______________
epoch 11 train loss 6.360962867736816
val loss 6.596761226654053
______________
epoch 12 train loss 6.218802452087402
val loss 6.47504472

epoch 105 train loss 1.8636438846588135
val loss 2.6292543411254883
______________
epoch 106 train loss 1.8696967363357544
val loss 2.628772020339966
______________
epoch 107 train loss 1.8522931337356567
val loss 2.6290159225463867
______________
epoch 108 train loss 1.865098237991333
val loss 2.6301639080047607
______________
epoch 109 train loss 1.8486413955688477
val loss 2.631396770477295
______________
epoch 110 train loss 1.8158602714538574
val loss 2.6338248252868652
______________
epoch 111 train loss 1.818355917930603
val loss 2.636157274246216
______________
epoch 112 train loss 1.8368574380874634
val loss 2.6382737159729004
______________
epoch 113 train loss 1.8429393768310547
val loss 2.640237331390381
______________
epoch 114 train loss 1.8179051876068115
val loss 2.641493558883667
______________
epoch 115 train loss 1.805047631263733
val loss 2.6427388191223145
______________
epoch 116 train loss 1.7970387935638428
val loss 2.643069267272949
______________
epoch 117 tra

(OutcomeSimulator(
   (input_dropout): Dropout(p=0.1, inplace=False)
   (layers): ModuleList(
     (0): Linear(in_features=78, out_features=100, bias=True)
     (1): ReLU()
   )
   (batchnorm): BatchNorm1d(100, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
   (dropout): Dropout(p=0.1, inplace=False)
   (relu): Softplus(beta=1, threshold=20)
   (sigmoid): Sigmoid()
   (softmax): LogSoftmax(dim=1)
   (disease_layer): Linear(in_features=100, out_features=3, bias=True)
   (nodal_disease_layer): Linear(in_features=100, out_features=3, bias=True)
   (dlt_layers): ModuleList(
     (0-7): 8 x Linear(in_features=100, out_features=1, bias=True)
   )
   (treatment_layer): Linear(in_features=100, out_features=4, bias=True)
 ),
 2.628772020339966,
 {'pd': {'accuracy': 0.34782608695652173,
   'auc_micro': 0.9258557800224467,
   'auc_mean': 0.6967917025369007,
   'auc_weighted': 0.6999114004104814},
  'nd': {'accuracy': 0.3132749107432652,
   'auc_micro': 0.7144043663977219,
   'auc

In [107]:
train_state(model_args=t1_args,state=2,lr=.001,weights=[1,1,.1,10],use_smote=True)

here
epoch 0 train loss 6.593403339385986
val loss 7.873807430267334
______________


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


epoch 1 train loss 6.456299304962158
val loss 7.711670875549316
______________
epoch 2 train loss 6.332012176513672
val loss 7.55325174331665
______________
epoch 3 train loss 6.207035541534424
val loss 7.397796630859375
______________
epoch 4 train loss 6.085976600646973
val loss 7.245410442352295
______________
epoch 5 train loss 5.963022232055664
val loss 7.095478534698486
______________
epoch 6 train loss 5.836241245269775
val loss 6.947819232940674
______________
epoch 7 train loss 5.719584941864014
val loss 6.80241584777832
______________
epoch 8 train loss 5.598799705505371
val loss 6.659438610076904
______________
epoch 9 train loss 5.496089935302734
val loss 6.518987655639648
______________
epoch 10 train loss 5.375589370727539
val loss 6.381009101867676
______________
epoch 11 train loss 5.2747673988342285
val loss 6.2452192306518555
______________
epoch 12 train loss 5.149298667907715
val loss 6.111172676086426
______________
epoch 13 train loss 5.035346508026123
val loss 5.

val loss 2.574834108352661
______________
best loss 2.5730886459350586 {'pd': {'accuracy': 0.3306233062330623, 'auc_micro': 0.9284979423868313, 'auc_mean': 0.7518872883080544, 'auc_weighted': 0.7328188999641138}, 'nd': {'accuracy': 0.32534891269068483, 'auc_micro': 0.7413621262458472, 'auc_mean': 0.5945833043800524, 'auc_weighted': 0.5225360046457608}, 'mod': {'accuracy': 0.32534891269068483, 'auc_micro': 0.7413621262458472, 'auc_mean': 0.5945833043800524, 'auc_weighted': 0.5225360046457608}, 'dlts': {'accuracy': [0.9523809523809523, 0.9795918367346939, 1.0, 0.9659863945578231, 1.0, 0.9659863945578231, 0.9183673469387755, 1.0], 'accuracy_mean': 0.9564625850340136, 'auc': [0.7459183673469387, 0.525462962962963, -1, 0.4746478873239437, -1, 0.6084507042253522, 0.7061728395061728, -1], 'auc_mean': 0.612130552273074}}


(OutcomeSimulator(
   (input_dropout): Dropout(p=0.1, inplace=False)
   (layers): ModuleList(
     (0): Linear(in_features=78, out_features=100, bias=True)
     (1): ReLU()
   )
   (batchnorm): BatchNorm1d(100, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
   (dropout): Dropout(p=0.1, inplace=False)
   (relu): Softplus(beta=1, threshold=20)
   (sigmoid): Sigmoid()
   (softmax): LogSoftmax(dim=1)
   (disease_layer): Linear(in_features=100, out_features=3, bias=True)
   (nodal_disease_layer): Linear(in_features=100, out_features=3, bias=True)
   (dlt_layers): ModuleList(
     (0-7): 8 x Linear(in_features=100, out_features=1, bias=True)
   )
   (treatment_layer): Linear(in_features=100, out_features=4, bias=True)
 ),
 2.5730886459350586,
 {'pd': {'accuracy': 0.3306233062330623,
   'auc_micro': 0.9284979423868313,
   'auc_mean': 0.7518872883080544,
   'auc_weighted': 0.7328188999641138},
  'nd': {'accuracy': 0.32534891269068483,
   'auc_micro': 0.7413621262458472,
   'au

In [120]:
def train_model_ensemble(model_arg_list,state,
                         n_bags=20,
                         smote_options=[True,False],
                         smote_baseline_options=[True,False],
                         weight_options=[None],
                         weight_baseline_options=[None],
                         **kwargs):
    resampled_models =[]
    base_models = []
    base_metrics = []
    resample_metrics = []
    base_losses = []
    resample_losses = []
    n_errors = 0
    for margs in model_arg_list:
        for s in smote_baseline_options:
            for w in weight_baseline_options:
                [base_model,blosses,bmetrics] = train_state(model_args=margs,state=state,
                                         resample_training=False,
                                         use_smote=smote_options,
                                         weights=w,
                                         verbose=False,**kwargs)
                base_models.append(base_model)
                base_metrics.append(bmetrics)
                base_losses.append(blosses)
        for n in range(n_bags):
            for s in smote_options:
                for w in weight_options:
                    #this can fail if I resample a bad distribution with no minority classes
                    done = False
                    while not done:
                        try:
                            [model,loss,metrics] = train_state(model_args=margs,
                                                state=state,resample_training=True,
                                                use_smote=s,
                                                weights=w,
                                                verbose=False,**kwargs)
                            resampled_models.append(model)
                            resample_metrics.append(metrics)
                            resample_losses.append(loss)
                            done=True
                            print('model_done',len(base_models)+len(resampled_models))
                        except Exception as e:
                            print('error training model')
                            print(e)
                            n_errors += 1
    print('done with',n_errors,'errors')
    return base_models,resampled_models

from Models import *

In [121]:
t1_arglist = [
     {'hidden_layers': [400,400], 'dropout': 0.5, 'input_dropout': 0.25},
     {'hidden_layers': [10,10], 'dropout': 0.1, 'input_dropout': .1},
]
m1_list, m1_ensemble = train_model_ensemble(t1_arglist,1,
                                            n_bags=10,
                                           )
from Models import *
emodel1 = TransitionEnsemble(m1_list,m1_ensemble)
test2 = emodel1(transition_sample(1)[0][0].view(1,-1).to(emodel1.get_device()))
test2

here


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 1.899892807006836 {'pd': {'accuracy': 0.47523809523809524, 'auc_micro': 0.798309948979592, 'auc_mean': 0.6376898094009699, 'auc_weighted': 0.6867069943404759}, 'nd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.8734567901234568, 'auc_mean': 0.5047362601868416, 'auc_weighted': 0.5436253561253561}, 'mod': {'accuracy': 0.3333333333333333, 'auc_micro': 0.8734567901234568, 'auc_mean': 0.5047362601868416, 'auc_weighted': 0.5436253561253561}, 'dlts': {'accuracy': [0.7857142857142857, 0.9464285714285714, 1.0, 0.9107142857142857, 1.0, 0.8928571428571429, 0.8035714285714286, 1.0], 'accuracy_mean': 0.8678571428571429, 'auc': [0.44886363636363635, 0.2830188679245283, -1, 0.6627450980392157, -1, 0.45999999999999996, 0.5313131313131313, -1], 'auc_mean': 0.47718814672810234}}
here


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 1.883916974067688 {'pd': {'accuracy': 0.499047619047619, 'auc_micro': 0.8163265306122449, 'auc_mean': 0.6626422441522553, 'auc_weighted': 0.7154465737266072}, 'nd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.8789798570500326, 'auc_mean': 0.5404437651654085, 'auc_weighted': 0.5751144528660252}, 'mod': {'accuracy': 0.3333333333333333, 'auc_micro': 0.8789798570500326, 'auc_mean': 0.5404437651654085, 'auc_weighted': 0.5751144528660252}, 'dlts': {'accuracy': [0.7857142857142857, 0.9464285714285714, 1.0, 0.9107142857142857, 1.0, 0.8928571428571429, 0.8035714285714286, 1.0], 'accuracy_mean': 0.8678571428571429, 'auc': [0.44507575757575757, 0.3962264150943396, -1, 0.7098039215686275, -1, 0.38666666666666666, 0.48484848484848486, -1], 'auc_mean': 0.48452424915077524}}
here


...

/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 2.8248963356018066 {'pd': {'accuracy': 0.3578915843066786, 'auc_micro': 0.6839765609213982, 'auc_mean': 0.5296966029649816, 'auc_weighted': 0.5565250722445986}, 'nd': {'accuracy': 0.30775316455696206, 'auc_micro': 0.7600081699346406, 'auc_mean': 0.3396399237929884, 'auc_weighted': 0.340917219658996}, 'mod': {'accuracy': 0.30775316455696206, 'auc_micro': 0.7600081699346406, 'auc_mean': 0.3396399237929884, 'auc_weighted': 0.340917219658996}, 'dlts': {'accuracy': [0.82, 0.95, 1.0, 0.88, 0.99, 0.86, 0.78, 0.98], 'accuracy_mean': 0.8942857142857142, 'auc': [0.4129464285714286, 0.4273684210526316, -1, 0.5170454545454545, -1, 0.36295681063122925, 0.42657342657342656, 0.32653061224489793], 'auc_mean': 0.41223685893651146}}
model_done 41
best loss 2.4475417137145996 {'pd': {'accuracy': 0.3299961494031575, 'auc_micro': 0.6842876854087616, 'auc_mean': 0.47258293689663394, 'auc_weighted': 0.5214899700267793}, 'nd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.851677559912854, 'auc_mea

/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 2.438791275024414 {'pd': {'accuracy': 0.4340659340659341, 'auc_micro': 0.8083498363173423, 'auc_mean': 0.6132608435178529, 'auc_weighted': 0.6818442939209467}, 'nd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.8606293106966493, 'auc_mean': 0.4249302143854227, 'auc_weighted': 0.4394567325753452}, 'mod': {'accuracy': 0.3333333333333333, 'auc_micro': 0.8606293106966493, 'auc_mean': 0.4249302143854227, 'auc_weighted': 0.4394567325753452}, 'dlts': {'accuracy': [0.8303571428571429, 0.9642857142857143, 0.9910714285714286, 0.9017857142857143, 1.0, 0.8660714285714286, 0.8482142857142857, 0.9910714285714286], 'accuracy_mean': 0.913265306122449, 'auc': [0.5087719298245614, 0.5416666666666667, -1, 0.4716471647164716, -1, 0.6371134020618556, 0.4904024767801857, -1], 'auc_mean': 0.5299203280099481}}
model_done 43
best loss 2.2732744216918945 {'pd': {'accuracy': 0.4155646754825962, 'auc_micro': 0.7854639175257732, 'auc_mean': 0.593889397886353, 'auc_weighted': 0.6701478063789534}, 'nd':

{'predictions': [tensor([[0.1160, 0.8696, 0.0144]], device='cuda:0', grad_fn=<MeanBackward1>),
  tensor([[0.0715, 0.8835, 0.0450]], device='cuda:0', grad_fn=<MeanBackward1>),
  tensor([[0.8261, 0.0271, 0.0253, 0.0297, 0.0249, 0.0426, 0.0243]],
         device='cuda:0', grad_fn=<MeanBackward1>),
  tensor([[0.0598, 0.0628, 0.0096, 0.0549, 0.0193, 0.0664, 0.0652, 0.0279]],
         device='cuda:0', grad_fn=<MeanBackward1>)],
 '5%': [tensor([[0.0558, 0.4606, 0.0140]], device='cuda:0', grad_fn=<ViewBackward0>),
  tensor([[0.0333, 0.6084, 0.0279]], device='cuda:0', grad_fn=<ViewBackward0>),
  tensor([[0.2591, 0.0253, 0.0194, 0.0253, 0.0182, 0.0514, 0.0181]],
         device='cuda:0', grad_fn=<ViewBackward0>),
  tensor([[0.0259, 0.0145, 0.0058, 0.0270, 0.0054, 0.0396, 0.0501, 0.0043]],
         device='cuda:0', grad_fn=<ViewBackward0>)],
 '95%': [tensor([[0.3844, 0.9254, 0.1345]], device='cuda:0', grad_fn=<ViewBackward0>),
  tensor([[0.2101, 0.9382, 0.1883]], device='cuda:0', grad_fn=<ViewBac

In [122]:
t2_arglist = [
    {'hidden_layers': [400], 'dropout': .9, 'input_dropout': .5},
     {'hidden_layers': [100], 'dropout': 0.9, 'input_dropout': 0.5},
]
m2_list, m2_ensemble = train_model_ensemble(t2_arglist,2,
                                            n_bags=10)
emodel2 = TransitionEnsemble(m2_list,m2_ensemble)
emodel2(transition_sample(2)[0][0].view(1,-1))

here


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 1.4132548570632935 {'pd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.9358164983164984, 'auc_mean': 0.6390752202429029, 'auc_weighted': 0.7117926285671858}, 'nd': {'accuracy': 0.3675430055176891, 'auc_micro': 0.7464878974845752, 'auc_mean': 0.5931259120283511, 'auc_weighted': 0.5322706155632985}, 'mod': {'accuracy': 0.3675430055176891, 'auc_micro': 0.7464878974845752, 'auc_mean': 0.5931259120283511, 'auc_weighted': 0.5322706155632985}, 'dlts': {'accuracy': [0.9523809523809523, 0.9795918367346939, 1.0, 0.9659863945578231, 1.0, 0.9659863945578231, 0.9183673469387755, 1.0], 'accuracy_mean': 0.9564625850340136, 'auc': [0.6683673469387754, 0.4629629629629629, -1, 0.47605633802816905, -1, 0.5816901408450704, 0.7154320987654321, -1], 'auc_mean': 0.580901777508082}}
here


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 1.4159045219421387 {'pd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.935512532734755, 'auc_mean': 0.6944204455364952, 'auc_weighted': 0.7127095332230229}, 'nd': {'accuracy': 0.33495618305744884, 'auc_micro': 0.7371143806359753, 'auc_mean': 0.5846254024506058, 'auc_weighted': 0.5120324719318623}, 'mod': {'accuracy': 0.33495618305744884, 'auc_micro': 0.7371143806359753, 'auc_mean': 0.5846254024506058, 'auc_weighted': 0.5120324719318623}, 'dlts': {'accuracy': [0.9523809523809523, 0.9795918367346939, 1.0, 0.9659863945578231, 1.0, 0.9659863945578231, 0.9183673469387755, 1.0], 'accuracy_mean': 0.9564625850340136, 'auc': [0.653061224489796, 0.46296296296296297, -1, 0.4830985915492958, -1, 0.6746478873239437, 0.7364197530864197, -1], 'auc_mean': 0.6020380838824837}}
here


...

/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 1.5145801305770874 {'pd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.9375256685913076, 'auc_mean': 0.525060770631583, 'auc_weighted': 0.6501396551259876}, 'nd': {'accuracy': 0.30735583825837254, 'auc_micro': 0.721823732803649, 'auc_mean': 0.4912154082440341, 'auc_weighted': 0.48662675998086347}, 'mod': {'accuracy': 0.30735583825837254, 'auc_micro': 0.721823732803649, 'auc_mean': 0.4912154082440341, 'auc_weighted': 0.48662675998086347}, 'dlts': {'accuracy': [0.9411764705882353, 0.9688581314878892, 1.0, 0.9653979238754326, 1.0, 0.9619377162629758, 0.9377162629757786, 0.9896193771626297], 'accuracy_mean': 0.9607843137254902, 'auc': [0.7071799307958477, 0.5357142857142857, -1, 0.5530465949820789, -1, 0.6386527141922825, 0.6730217302173022, 0.7657342657342657], 'auc_mean': 0.6455582536060105}}
model_done 41
best loss 1.4357154369354248 {'pd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.9344374037514831, 'auc_mean': 0.5834565819062446, 'auc_weighted': 0.6304391658345495}, 

/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 1.5781114101409912 {'pd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.8924105083350997, 'auc_mean': 0.5723804851759674, 'auc_weighted': 0.6349646879370673}, 'nd': {'accuracy': 0.34140110259513246, 'auc_micro': 0.7600316555872112, 'auc_mean': 0.5779178929603332, 'auc_weighted': 0.5515647289582224}, 'mod': {'accuracy': 0.34140110259513246, 'auc_micro': 0.7600316555872112, 'auc_mean': 0.5779178929603332, 'auc_weighted': 0.5515647289582224}, 'dlts': {'accuracy': [0.9578947368421052, 0.9649122807017544, 1.0, 0.9719298245614035, 0.9964912280701754, 0.9789473684210527, 0.9473684210526315, 0.9894736842105263], 'accuracy_mean': 0.9724310776942355, 'auc': [0.7228327228327228, 0.5829090909090908, -1, 0.5672382671480145, -1, 0.7168458781362007, 0.654567901234568, 0.6713947990543735], 'auc_mean': 0.6526314432191618}}
model_done 43
best loss 1.5235663652420044 {'pd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.934426133364612, 'auc_mean': 0.6123815727998924, 'auc_weighted': 0.67394

{'predictions': [tensor([[0.7200, 0.2614, 0.0187]], device='cuda:0', grad_fn=<MeanBackward1>),
  tensor([[0.4618, 0.5073, 0.0309]], device='cuda:0', grad_fn=<MeanBackward1>),
  tensor([[0.0746, 0.6989, 0.1766, 0.0499]], device='cuda:0',
         grad_fn=<MeanBackward1>),
  tensor([[0.0654, 0.0288, 0.0024, 0.0644, 0.0027, 0.0219, 0.0484, 0.0230]],
         device='cuda:0', grad_fn=<MeanBackward1>)],
 '5%': [tensor([[0.6512, 0.1149, 0.0182]], device='cuda:0', grad_fn=<ViewBackward0>),
  tensor([[0.3758, 0.4193, 0.0158]], device='cuda:0', grad_fn=<ViewBackward0>),
  tensor([[0.0534, 0.5153, 0.1104, 0.0381]], device='cuda:0',
         grad_fn=<ViewBackward0>),
  tensor([[0.0376, 0.0155, 0.0024, 0.0321, 0.0027, 0.0124, 0.0352, 0.0106]],
         device='cuda:0', grad_fn=<ViewBackward0>)],
 '95%': [tensor([[0.8344, 0.3193, 0.0813]], device='cuda:0', grad_fn=<ViewBackward0>),
  tensor([[0.5271, 0.5838, 0.0689]], device='cuda:0', grad_fn=<ViewBackward0>),
  tensor([[0.1601, 0.7810, 0.2397, 0.0

In [123]:
t3_arglist = [
     {'hidden_layers': [10,10], 'dropout': 0.25, 'input_dropout': .25},
    {'hidden_layers': [100], 'dropout': 0.9, 'input_dropout': 0},
]
m3_list, m3_ensemble = train_model_ensemble(t3_arglist,3,n_bags=10,
                                           )
emodel3 = EndpointEnsemble(m3_list,m3_ensemble)
emodel3(transition_sample(3)[0][0].view(1,-1))

here


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and

/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMe

/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMe

/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMe

...

best loss 1.824763298034668 {'Overall Survival (4 Years)': {'accuracy': 0.8581081081081081, 'mse': 0.13172078, 'auc': 0.4945002391200382, 'precision': 0.8610169491525423, 'recall': 0.996078431372549, 'f1': 0.9236363636363637}, 'FT': {'accuracy': 0.7905405405405406, 'mse': 0.163326, 'auc': 0.6324786324786326, 'precision': 0.0, 'recall': 0.0, 'f1': 0.0}, 'Aspiration rate Post-therapy': {'accuracy': 0.8209459459459459, 'mse': 0.14512713, 'auc': 0.6362295209255375, 'precision': 0.0, 'recall': 0.0, 'f1': 0.0}, 'LRC': {'accuracy': 0.875, 'mse': 0.11805308, 'auc': 0.5558802045288532, 'precision': 0.875, 'recall': 1.0, 'f1': 0.9333333333333333}}
model_done 43


/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMe

/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMe

best loss 1.9063925743103027 {'Overall Survival (4 Years)': {'accuracy': 0.8639455782312925, 'mse': 0.1307529, 'auc': 0.481003937007874, 'precision': 0.8639455782312925, 'recall': 1.0, 'f1': 0.927007299270073}, 'FT': {'accuracy': 0.8129251700680272, 'mse': 0.14973675, 'auc': 0.6166603271205782, 'precision': 0.0, 'recall': 0.0, 'f1': 0.0}, 'Aspiration rate Post-therapy': {'accuracy': 0.8163265306122449, 'mse': 0.14550431, 'auc': 0.6690586419753086, 'precision': 0.0, 'recall': 0.0, 'f1': 0.0}, 'LRC': {'accuracy': 0.8571428571428571, 'mse': 0.13418189, 'auc': 0.5654761904761906, 'precision': 0.8571428571428571, 'recall': 1.0, 'f1': 0.923076923076923}}
model_done 44
done with 0 errors


{'predictions': tensor([[0.7779, 0.2404, 0.2446, 0.7946]], device='cuda:0',
        grad_fn=<MeanBackward1>),
 '5%': tensor([[0.6430, 0.1934, 0.2064, 0.7136]], device='cuda:0',
        grad_fn=<ViewBackward0>),
 '95%': tensor([[0.8147, 0.3604, 0.3842, 0.8943]], device='cuda:0',
        grad_fn=<ViewBackward0>)}

In [ ]:
len(emodel3.base_models)

In [24]:
def gridsearch_attention_transition_models(state=1,attentions=[False]):
    hiddenlayers = [[10],[50],[100],[400],[1000,100],[10,10],[50,50],[100,100],[400,400]]
    model_arglist = [{'hidden_layers': h} for h in hiddenlayers]
    best_loss = 100000000000
    best_metrics = {}
    best_args = {}
    best_model = None
    k = 0
    records = []
    for margs in model_arglist:
        args = {k:v for k,v in margs.items()}
        for use_smote in [True,False]:
            for dropout in [0,.1,.25,.5,.9]:
                args['dropout'] = dropout
                for input_dropout in [0,.1,.25,.5]:
                    args['input_dropout'] = input_dropout
                    model,m_loss,m_metrics = train_state(
                        model_args=args,
                        state=state,
                        lr=.001,
                        use_smote=use_smote,
                        use_attention=False,
                        verbose=False)
                    newargs = {k:copy.deepcopy(v) for k,v in args.items()}
                    newargs['use_smote'] = use_smote
                    record = {'loss': m_loss,'metrics':m_metrics,'args':newargs,'model': model}
                    records.append(record)
                    print('done',k,m_loss)
                    k+=1
                    if m_loss < best_loss:
                        best_loss = m_loss
                        best_metrics  = m_metrics
                        best_model = model
                        best_args = {k:v for k,v in args.items()}
                        best_args['smote'] = use_smote
                        print('_++++++++++New Best++++____')
                        print(best_loss)
                        print(best_metrics)
                        print(best_args)
                        print(use_smote)
                        print('___________')
                        print('++++++++')
                        print()
    print('_________')
    print('+++++++++++')
    print('best stuff',best_loss)
    print(best_metrics)
    print(best_args)
    return best_model, records
# model1_gs = gridsearch_attention_transition_models(1)
# model1_gs[0]

In [25]:
# model2_gs = gridsearch_attention_transition_models(2)
# model2_gs[0]

In [26]:
# model3_gs= gridsearch_attention_transition_models(3)
# model3_gs[0]

here


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 1.8314793109893799 {'Overall Survival (4 Years)': {'accuracy': 0.8571428571428571, 'mse': 0.1243038, 'auc': 0.4770992366412214, 'precision': 0.9104477611940298, 'recall': 0.9312977099236641, 'f1': 0.9207547169811321}, 'FT': {'accuracy': 0.7619047619047619, 'mse': 0.16614403, 'auc': 0.6635869565217392, 'precision': 0.4117647058823529, 'recall': 0.21875, 'f1': 0.2857142857142857}, 'Aspiration rate Post-therapy': {'accuracy': 0.8231292517006803, 'mse': 0.14100426, 'auc': 0.7946598855689765, 'precision': 0.5, 'recall': 0.46153846153846156, 'f1': 0.48000000000000004}, 'LRC': {'accuracy': 0.8639455782312925, 'mse': 0.12312649, 'auc': 0.47727272727272724, 'precision': 0.9, 'recall': 0.9545454545454546, 'f1': 0.9264705882352942}}
done 0 1.8314793109893799
_++++++++++New Best++++____
1.8314793109893799
{'Overall Survival (4 Years)': {'accuracy': 0.8571428571428571, 'mse': 0.1243038, 'auc': 0.4770992366412214, 'precision': 0.9104477611940298, 'recall': 0.9312977099236641, 'f1': 0.92075

/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 1.7722574472427368 {'Overall Survival (4 Years)': {'accuracy': 0.8571428571428571, 'mse': 0.12560907, 'auc': 0.46564885496183206, 'precision': 0.8985507246376812, 'recall': 0.9465648854961832, 'f1': 0.9219330855018587}, 'FT': {'accuracy': 0.7619047619047619, 'mse': 0.17506051, 'auc': 0.6516304347826086, 'precision': 0.4, 'recall': 0.1875, 'f1': 0.25531914893617025}, 'Aspiration rate Post-therapy': {'accuracy': 0.7891156462585034, 'mse': 0.13096674, 'auc': 0.7965670692943421, 'precision': 0.3684210526315789, 'recall': 0.2692307692307692, 'f1': 0.3111111111111111}, 'LRC': {'accuracy': 0.8843537414965986, 'mse': 0.11268359, 'auc': 0.6227272727272728, 'precision': 0.9078014184397163, 'recall': 0.9696969696969697, 'f1': 0.9377289377289377}}
done 1 1.7722574472427368
_++++++++++New Best++++____
1.7722574472427368
{'Overall Survival (4 Years)': {'accuracy': 0.8571428571428571, 'mse': 0.12560907, 'auc': 0.46564885496183206, 'precision': 0.8985507246376812, 'recall': 0.946564885496183

...

best loss 1.5873210430145264 {'Overall Survival (4 Years)': {'accuracy': 0.891156462585034, 'mse': 0.10515472, 'auc': 0.5658396946564885, 'precision': 0.891156462585034, 'recall': 1.0, 'f1': 0.9424460431654677}, 'FT': {'accuracy': 0.782312925170068, 'mse': 0.15795794, 'auc': 0.7114130434782608, 'precision': 0.5, 'recall': 0.09375, 'f1': 0.15789473684210525}, 'Aspiration rate Post-therapy': {'accuracy': 0.8095238095238095, 'mse': 0.12177198, 'auc': 0.8038779402415765, 'precision': 0.375, 'recall': 0.11538461538461539, 'f1': 0.1764705882352941}, 'LRC': {'accuracy': 0.8979591836734694, 'mse': 0.09483484, 'auc': 0.6292929292929292, 'precision': 0.8979591836734694, 'recall': 1.0, 'f1': 0.9462365591397849}}
done 358 1.5873210430145264


/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMe

/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMe

best loss 1.5910322666168213 {'Overall Survival (4 Years)': {'accuracy': 0.891156462585034, 'mse': 0.11064984, 'auc': 0.5667938931297709, 'precision': 0.891156462585034, 'recall': 1.0, 'f1': 0.9424460431654677}, 'FT': {'accuracy': 0.7959183673469388, 'mse': 0.15551725, 'auc': 0.7182065217391305, 'precision': 0.6666666666666666, 'recall': 0.125, 'f1': 0.21052631578947367}, 'Aspiration rate Post-therapy': {'accuracy': 0.8027210884353742, 'mse': 0.12270794, 'auc': 0.8032422123331214, 'precision': 0.2, 'recall': 0.038461538461538464, 'f1': 0.06451612903225806}, 'LRC': {'accuracy': 0.8979591836734694, 'mse': 0.09806414, 'auc': 0.6540404040404041, 'precision': 0.8979591836734694, 'recall': 1.0, 'f1': 0.9462365591397849}}
done 359 1.5910322666168213
_________
+++++++++++
best stuff 1.539259672164917
{'Overall Survival (4 Years)': {'accuracy': 0.891156462585034, 'mse': 0.106308855, 'auc': 0.5596374045801527, 'precision': 0.891156462585034, 'recall': 1.0, 'f1': 0.9424460431654677}, 'FT': {'accu

EndpointSimulator(
  (input_dropout): Dropout(p=0.25, inplace=False)
  (layers): ModuleList(
    (0): Linear(in_features=76, out_features=50, bias=True)
    (1): ReLU()
    (2): Linear(in_features=50, out_features=50, bias=True)
    (3): ReLU()
  )
  (batchnorm): BatchNorm1d(50, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (dropout): Dropout(p=0.25, inplace=False)
  (relu): Softplus(beta=1, threshold=20)
  (sigmoid): Sigmoid()
  (softmax): LogSoftmax(dim=1)
  (outcome_layer): Linear(in_features=50, out_features=4, bias=True)
)

In [27]:
# [(m['args'],m['loss']) for m in sorted(model1_gs[1], key = lambda x: x['loss'])]

In [28]:
# [(m['args'],m['loss']) for m in sorted(model2_gs[1], key = lambda x: x['loss'])]

In [29]:
# [(m['args'],m['loss']) for m in sorted(model3_gs[1], key = lambda x: x['loss'])]

In [ ]:
# def load_trained_models():
#     files = Const.tuned_transition_models
#     decision_file = Const.tuned_decision_model
#     [model1,model2,model3] = [torch.load(file) for file in files]
#     decision_model = torch.load(decision_file)
#     return decision_model, model1,model2,model3
# _, model1, model2, model3 =load_trained_models()

In [35]:
def calc_optimal_decisions(dataset,ids,m1,m2,m3,weights=[-1,1,1,-1],outcome_loss_func=None,get_transitions=True):
    m1.eval()
    m2.eval()
    m3.eval()
    device = m1.get_device()
    data = dataset.processed_df.copy().loc[ids]
    
    def get_dlt(state):
        if state == 2:
            return data[Const.dlt2].copy()
        d = data[Const.dlt1].copy()
        if state < 1:
            d.values[:,:] = 0
        return d
    
    def get_pd(state):
        if state == 2:
            return data[Const.primary_disease_states2].copy()
        d = data[Const.primary_disease_states].copy()
        if state < 1:
            d.values[:,:] = 0
        return d
    
    def get_nd(state):
        if state == 2:
            return data[Const.nodal_disease_states2].copy()
        d = data[Const.nodal_disease_states].copy()
        if state < 1:
            d.values[:,:] = 0
        return d
    
    def get_cc(state):
        res = data[Const.ccs].copy()
        if state == 1:
            res.values[:,:] = np.zeros(res.values.shape)
        return res
    
    def get_mod(state):
        res = data[Const.modifications].copy()
        #this should have an ic condition but we don't use it anumore anywa
        return res
        
    def formatdf(d):
        d = df_to_torch(d).to(device)
        return d
    
    
    outcomedf = data[Const.outcomes]
    baseline = dataset.get_state('baseline').loc[ids]
    baseline_input = formatdf(baseline)

    
    def outcome_loss(ypred):
        l = torch.mul((-1*(ypred[:,0] - 1)),-weights[0])
        for i,weight in enumerate(weights[1:]):
            #weights with negative values will invert the outcome so e.g. Regional control becomes no regional control
            #so the penaly is correct
            if weight > 0:
                newloss = torch.mul(ypred[:,i],weight)
            else:
                newloss = torch.mul(-1*(ypred[:,i] - 1),-weights[i])
            l = torch.add(l,newloss)
        return l
    if outcome_loss_func is None:
        outcome_loss_func = outcome_loss
    
    cat = lambda x: torch.cat([xx.to(device) for xx in x],axis=1).to(device)
    format_transition = lambda x: x.to(device)
    
    def get_outcome(d1,d2,d3):
        d1 = torch.full((len(ids),1),d1).type(torch.FloatTensor)
        d2 = torch.full((len(ids),1),d2).type(torch.FloatTensor)
        d3 = torch.full((len(ids),1),d3).type(torch.FloatTensor)
        
        tinput1 = cat([baseline_input,d1])
        ytransition = m1(tinput1)
        [ypd1,ynd1,ymod,ydlt1] = [format_transition(xx) for xx in ytransition['predictions']]
        d1_thresh = torch.gt(d1,.5).view(-1,1).to(device)
        ypd1[:,0:2] = ypd1[:,0:2]*d1_thresh
        ynd1[:,0:2] = ynd1[:,0:2]*d1_thresh
        
        tinput2 = cat([baseline_input,ypd1,ynd1,ymod,ydlt1,d1,d2])
        ytransition2 = m2(tinput2)
        [ypd2,ynd2,ycc,ydlt2] = [format_transition(xx) for xx in ytransition2['predictions']]
        
        input3 = cat([baseline_input, ypd2, ynd2, ycc, ydlt2, d1, d2,d3])
        outcome = m3(input3)['predictions']
        transitions = {
            'pd1': ypd1,
            'nd1': ynd1,
            'nd2': ynd2,
            'pd2': ypd2,
            'mod': ymod,
            'cc': ycc,
            'dlt1': ydlt1,
            'dlt2': ydlt2,
        }
        return outcome, transitions

    losses = []
    loss_order = []
    transitions = {}
    for d1 in [0,1]:
        for d2 in [0,1]:
            for d3 in [0,1]:
                outcomes, transition_entry = get_outcome(d1,d2,d3)
                loss = outcome_loss_func(outcomes)
                losses.append(loss)
                loss_order.append([d1,d2,d3])
                transitions[str(d1)+str(d2)+str(d3)] = transition_entry
    losses = torch.stack(losses,axis=1)
    optimal_decisions = [loss_order[i] for i in torch.argmin(losses,axis=1)]
    result = torch.tensor(optimal_decisions).type(torch.FloatTensor)
    if get_transitions:
        opt_transitions = {k: torch.zeros(v.shape).type(torch.FloatTensor) for k,v in transitions['000'].items()}
        for i,od in enumerate(optimal_decisions):
            key = ''.join([str(o) for o in od])
            entry = transitions[key]
            for kk,vv in entry.items():
                opt_transitions[kk][i,:] = vv[i,:]
        return result, opt_transitions
    return result

test, testtest = get_tt_split()
calc_optimal_decisions(DTDataset(),testtest,emodel1,emodel2,emodel3)

(tensor([[1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [0., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1

In [39]:
    
def train_decision_model(
    tmodel1,
    tmodel2,
    tmodel3,
    use_default_split=True,
    use_bagging_split=False,
    lr=.0001,
    epochs=10000,
    patience=50,
    weights=[-1,1,1,-1], #realtive weight of survival, feeding tube, aspiration, andl lrc
    opt_weights=[1,1,1],
    imitation_weights=[.5,1,1],#weights of imitation decisions, because ic overtrains too quickly
    imitation_weight=1,
    shufflecol_chance = 0.1,
    reward_weight=1,
    split=.7,
    resample_training=False,
    save_path='../data/models/',
    file_suffix='',
    use_attention=True,
    verbose=True,
    use_smote=False,
    validate_with_memory=True,
    **model_kwargs,
):
    tmodel1.eval()
    tmodel2.eval()
    tmodel3.eval()

    train_ids, test_ids = get_tt_split(use_default_split=use_default_split,use_bagging_split=use_bagging_split,resample_training=resample_training)
    true_ids = train_ids + test_ids #for saving memory without upsampling
    if use_smote:
        dataset = DTDataset(use_smote=True,smote_ids = train_ids)
        train_ids = [i for i in dataset.processed_df.index.values if i not in test_ids]
    else:
        dataset = DTDataset()
    data = dataset.processed_df.copy()
    
    def get_dlt(state):
        if state == 2:
            return data[Const.dlt2].copy()
        d = data[Const.dlt1].copy()
        if state < 1:
            d.values[:,:] = 0
        return d
    
    def get_pd(state):
        if state == 2:
            return data[Const.primary_disease_states2].copy()
        d = data[Const.primary_disease_states].copy()
        if state < 1:
            d.values[:,:] = 0
        return d
    
    def get_nd(state):
        if state == 2:
            return data[Const.nodal_disease_states2].copy()
        d = data[Const.nodal_disease_states].copy()
        if state < 1:
            d.values[:,:] = 0
        return d
    
    def get_cc(state):
        res = data[Const.ccs].copy()
        if state == 1:
            res.values[:,:] = np.zeros(res.values.shape)
        return res
    
    def get_mod(state):
        res = data[Const.modifications].copy()
        #this should have an ic condition but we don't use it anumore anywa
        return res
        
    outcomedf = data[Const.outcomes]
    baseline = dataset.get_state('baseline')
    
    def formatdf(d,dids=train_ids):
        d = df_to_torch(d.loc[dids]).to(model.get_device())
        return d
    
    def makegrad(v):
        if not v.requires_grad:
            v.requires_grad=True
        return v
    
    if use_attention:
        model = DecisionAttentionModel(baseline.shape[1],**model_kwargs)
    else:
        model_kwargs = {k:v for k,v in model_kwargs.items() if 'attention' not in k and 'embed' not in k}
        model = DecisionModel(baseline.shape[1],**model_kwargs)

    hashcode = str(hash(','.join([str(i) for i in train_ids])))
    
    save_file = save_path + 'model_' + model.identifier +'_hash' + hashcode + file_suffix + '.tar'
    model.fit_normalizer(df_to_torch(baseline.loc[train_ids]))
    optimizer = torch.optim.Adam(model.parameters(),lr=lr)
    
    
    optimal_train,transitions_train = calc_optimal_decisions(dataset,train_ids,tmodel1,tmodel2,tmodel3,
                                           weights=weights,
                                          )
    optimal_test,transitions_test = calc_optimal_decisions(dataset,test_ids,tmodel1,tmodel2,tmodel3,
                                          weights=weights,
                                         )
    optimal_train = optimal_train.to(model.get_device())
    optimal_test = optimal_test.to(model.get_device())
    mse = torch.nn.MSELoss()
    nllloss = torch.nn.NLLLoss()
    bce = torch.nn.BCELoss()
    
    def compare_decisions(d1,d2,d3,ids):
#         ypred = np.concatenate([dd.cpu().detach().numpy().reshape(-1,1) for dd in [d1,d2,d3]],axis=1)
        ytrue = df_to_torch(outcomedf.loc[ids])
        dloss = bce(d1.view(-1),ytrue[:,0])
        dloss += bce(d2.view(-1),ytrue[:,1])
        dloss += bce(d3,view(-1),ytrue[:,2])
        return dloss
        
    def remove_decisions(df):
        cols = [c for c in df.columns if c not in Const.decisions ]
        ddf = df[cols]
        return ddf
    
    makeinput = lambda step,dids: df_to_torch(remove_decisions(dataset.get_input_state(step=step,ids=dids)))
    threshold = lambda x: torch.gt(x,torch.rand(x.shape[0])).type(torch.FloatTensor)

    
    #save the inputs from the whole dataset for future reference
    if use_attention:
        full_data = []
        for mstep in [0,1,2]:
            full_data_step = [baseline, get_dlt(min(mstep,1)),
                         get_dlt(mstep),get_pd(mstep),get_nd(mstep),get_cc(mstep),get_mod(mstep)]
            full_data_step = torch.cat([formatdf(fd,true_ids) for fd in full_data_step],axis=1)
            full_data.append(full_data_step)
        full_data = torch.stack(full_data)
        model.save_memory(full_data)
        print(full_data.shape)
    def step(train=True):
        if train:
            model.train(True)
            tmodel1.train(True)
            tmodel2.train(True)
            tmodel3.train(True)
            optimizer.zero_grad()
            ids = train_ids
            y_opt = makegrad(optimal_train)
            transition_dict = {k: torch.clone(v).detach() for k,v in transitions_train.items()}
        else:
            ids = test_ids
            model.eval()
            tmodel1.eval()
            tmodel2.eval()
            tmodel3.eval()
            y_opt = makegrad(optimal_test)
            transition_dict = {k: torch.clone(v).detach() for k,v in transitions_test.items()}
            
        ytrain = df_to_torch(outcomedf.loc[ids])
        #imitation losses and decision 1
        xxtrained = [baseline, get_dlt(0),get_dlt(0),get_pd(0),get_nd(0),get_cc(0),get_mod(0)]
        xxtrain = [formatdf(xx,ids) for xx in xxtrained]
        
        use_memory = (not train) and validate_with_memory
        if use_attention:
            o1 = model(torch.cat(xxtrain,axis=1),position=0,use_saved_memory = use_memory)
        else:
            o1 = model(torch.cat(xxtrain,axis=1),position=0)
        decision1_imitation = o1[:,3]
        decision1_opt = o1[:,0]
    

        imitation_loss1 = bce(decision1_imitation,ytrain[:,0])
        imitation_loss1 = torch.mul(imitation_loss1,imitation_weights[0])
        opt_loss1 = bce(decision1_opt,y_opt[:,0])
        opt_loss1 = torch.mul(opt_loss1,opt_weights[0])
        
        x1_imitation = [baseline, get_dlt(1),get_dlt(0),get_pd(1),get_nd(1),get_cc(1),get_mod(1)]
        x1_imitation = [formatdf(xx1,ids) for xx1 in x1_imitation]
        
        if use_attention:
            o2 = model(torch.cat(x1_imitation,axis=1),position=1,use_saved_memory = use_memory)
        else:
            o2 = model(torch.cat(x1_imitation,axis=1),position=1)
            
        decision2_imitation = o2[:,4]
            
        imitation_loss2 =  bce(decision2_imitation,ytrain[:,1])
        imitation_loss2 = torch.mul(imitation_loss2,imitation_weights[1])
        
        
        x2_imitation = [baseline, get_dlt(1),get_dlt(2),get_pd(2),get_nd(2),get_cc(2),get_mod(2)]
        
        x2_imitation = [formatdf(xx2,ids) for xx2 in x2_imitation]
        
        if use_attention:
            o3 = model(torch.cat(x2_imitation,axis=1),position=2,use_saved_memory = use_memory)
        else:
            o3 = model(torch.cat(x2_imitation,axis=1),position=2)
            
        decision3_imitation = o3[:,5]
        
        
        imitation_loss3 = bce(decision3_imitation,ytrain[:,2])
        imitation_loss3 = torch.mul(imitation_loss3,imitation_weights[2])
        
        opt_input2 = [
            formatdf(baseline,ids), 
            transition_dict['dlt1'],
            formatdf(get_dlt(0),ids),
            transition_dict['pd1'],
            transition_dict['nd1'], 
            formatdf(get_cc(0),ids),
            transition_dict['mod']
                 ]
        if use_attention:
            decision2_opt = model(torch.cat(opt_input2,axis=1),position=1,use_saved_memory=use_memory)[:,1]
        else:
            decision2_opt = model(torch.cat(opt_input2,axis=1),position=1)[:,1]
        
        opt_loss2 = bce(decision2_opt,y_opt[:,1])
        opt_loss2 = torch.mul(opt_loss2,opt_weights[1])
        
        opt_input3 = [
            formatdf(baseline,ids),
            transition_dict['dlt1'],
            transition_dict['dlt2'],
            transition_dict['pd2'],
            transition_dict['nd1'],
            transition_dict['cc'],
            transition_dict['mod'],
        ]
        
        if use_attention:
            decision3_opt = model(torch.cat(opt_input3,axis=1),position=2,use_saved_memory=use_memory)[:,2]
        else:
            decision3_opt = model(torch.cat(opt_input3,axis=1),position=2)[:,2]
        
        opt_loss3 = bce(decision3_opt,y_opt[:,2])
        opt_loss3 = torch.mul(opt_loss3,opt_weights[2])
        
        iloss = torch.add(torch.add(imitation_loss1,imitation_loss2),imitation_loss3)
        iloss = torch.mul(iloss,imitation_weight)
        
        reward_loss = torch.add(torch.add(opt_loss1,opt_loss2),opt_loss3)
        reward_loss =torch.mul(reward_loss,reward_weight)
        
        loss = torch.add(iloss,reward_loss)
        losses = [iloss,reward_loss]
        if train:
            loss.backward()
            optimizer.step()
            return losses
        else:
            scores = []
            distributions = [decision1_opt.mean().item(),decision2_opt.mean().item(),decision3_opt.mean().item()]
            imitation = [decision1_imitation,decision2_imitation,decision3_imitation]
            optimal = [decision1_opt,decision2_opt,decision3_opt]
            for i,decision_im in enumerate(imitation):
                deci = decision_im.cpu().detach().numpy()
                deci0 = (deci > .5).astype(int)
                iout = ytrain[:,i].cpu().detach().numpy()
                acci = accuracy_score(iout,deci0)
                try:
                    auci = roc_auc_score(iout,deci)
                except:
                    auci = -1
                
                deco = optimal[i].cpu().detach().numpy()
                deci0 = (deco > .5).astype(int)
                oout = y_opt[:,i].cpu().detach().numpy()
                acco = accuracy_score(oout,deci0)
                try:
                    auco = roc_auc_score(oout,deco)
                except:
                    auco=-1
                scores.append({'decision': i,'optimal_auc': acco,'imitation_auc': auci,'optimal_acc': acco,'imitation_acc': acci})
            return losses, scores, distributions
        
    best_val_loss = torch.tensor(1000000000.0)
    steps_since_improvement = 0
    best_val_score = {}
    
    for epoch in range(epochs):
        losses = step(True)
        val_losses,val_metrics,val_distributions = step(False)
        vl = 0
        for vm in val_metrics:
            vl += -((vm['optimal_auc']*reward_weight) + (vm['imitation_auc']*imitation_weight))
        if verbose:
            print('______epoch',str(epoch),'_____')
            print('val reward',val_losses[1].item())
            print('imitation reward', val_losses[0].item())
            print('distributions',val_distributions)
            print(val_metrics)
        if vl < best_val_loss:
            best_val_loss = vl
            best_val_score = val_metrics
            best_val_distributions = val_distributions
            steps_since_improvement = 0
            torch.save(model.state_dict(),save_file)
        else:
            steps_since_improvement += 1
        if steps_since_improvement > patience:
            break
    print('++++++++++Final+++++++++++')
    print('best',best_val_loss)
    print(best_val_score)
    model.load_state_dict(torch.load(save_file))
    model.eval()
    return model, best_val_score, best_val_loss, best_val_distributions

from Models import *
args = {
    'hidden_layers': [1000], 
    'attention_heads': [5],
    'embed_size': 120, 
    'dropout': 0.75, 
    'input_dropout': 0.5, 
    'shufflecol_chance':  0.1,
}

#1.8424
# decision_model, decision_score, decision_loss, _ = train_decision_model(
#     emodel1,emodel2,emodel3,
#     lr=.01,
#     imitation_weight=1,
#     reward_weight=1,
#     validate_with_memory=True,
#     use_smote=False,
#     use_attention=False,
#     verbose=True,
#     **args)

______epoch 0 _____
val reward 0.4495045840740204
imitation reward 1.374599814414978
distributions [0.8885024785995483, 0.08592654019594193, 0.07723517715930939]
[{'decision': 0, 'optimal_auc': 0.9727891156462585, 'imitation_auc': 0.28196564885496184, 'optimal_acc': 0.9727891156462585, 'imitation_acc': 0.891156462585034}, {'decision': 1, 'optimal_auc': 1.0, 'imitation_auc': 0.51875, 'optimal_acc': 1.0, 'imitation_acc': 0.782312925170068}, {'decision': 2, 'optimal_auc': 0.9727891156462585, 'imitation_auc': 0.41417673235855057, 'optimal_acc': 0.9727891156462585, 'imitation_acc': 0.8231292517006803}]
______epoch 1 _____
val reward 0.28324800729751587
imitation reward 1.474853515625
distributions [0.9782025814056396, 0.010871697217226028, 0.011503451503813267]
[{'decision': 0, 'optimal_auc': 0.9727891156462585, 'imitation_auc': 0.3125, 'optimal_acc': 0.9727891156462585, 'imitation_acc': 0.891156462585034}, {'decision': 1, 'optimal_auc': 1.0, 'imitation_auc': 0.6619565217391304, 'optimal_ac

______epoch 14 _____
val reward 0.1325075775384903
imitation reward 1.1374387741088867
distributions [0.9754704833030701, 0.000991534674540162, 0.028933856636285782]
[{'decision': 0, 'optimal_auc': 0.9795918367346939, 'imitation_auc': 0.54293893129771, 'optimal_acc': 0.9795918367346939, 'imitation_acc': 0.8775510204081632}, {'decision': 1, 'optimal_auc': 1.0, 'imitation_auc': 0.716304347826087, 'optimal_acc': 1.0, 'imitation_acc': 0.7755102040816326}, {'decision': 2, 'optimal_auc': 0.9863945578231292, 'imitation_auc': 0.8509218054672599, 'optimal_acc': 0.9863945578231292, 'imitation_acc': 0.8163265306122449}]
______epoch 15 _____
val reward 0.13295871019363403
imitation reward 1.142723560333252
distributions [0.9750352501869202, 0.0009435666725039482, 0.02915266342461109]
[{'decision': 0, 'optimal_auc': 0.9795918367346939, 'imitation_auc': 0.5534351145038168, 'optimal_acc': 0.9795918367346939, 'imitation_acc': 0.8843537414965986}, {'decision': 1, 'optimal_auc': 1.0, 'imitation_auc': 0.

______epoch 28 _____
val reward 0.15806949138641357
imitation reward 1.4174001216888428
distributions [0.9880443811416626, 0.0007977380300872028, 0.019661398604512215]
[{'decision': 0, 'optimal_auc': 0.9795918367346939, 'imitation_auc': 0.5567748091603053, 'optimal_acc': 0.9795918367346939, 'imitation_acc': 0.8639455782312925}, {'decision': 1, 'optimal_auc': 1.0, 'imitation_auc': 0.6997282608695652, 'optimal_acc': 1.0, 'imitation_acc': 0.7619047619047619}, {'decision': 2, 'optimal_auc': 0.9727891156462585, 'imitation_auc': 0.8089637635092181, 'optimal_acc': 0.9727891156462585, 'imitation_acc': 0.8299319727891157}]
______epoch 29 _____
val reward 0.15976262092590332
imitation reward 1.4728245735168457
distributions [0.9881274104118347, 0.0008113325457088649, 0.01977629028260708]
[{'decision': 0, 'optimal_auc': 0.9795918367346939, 'imitation_auc': 0.5539122137404581, 'optimal_acc': 0.9795918367346939, 'imitation_acc': 0.8571428571428571}, {'decision': 1, 'optimal_auc': 1.0, 'imitation_au

______epoch 43 _____
val reward 0.16466544568538666
imitation reward 1.869168758392334
distributions [0.988255500793457, 0.0005559640703722835, 0.019476478919386864]
[{'decision': 0, 'optimal_auc': 0.9795918367346939, 'imitation_auc': 0.5314885496183206, 'optimal_acc': 0.9795918367346939, 'imitation_acc': 0.8571428571428571}, {'decision': 1, 'optimal_auc': 1.0, 'imitation_auc': 0.6807065217391305, 'optimal_acc': 1.0, 'imitation_acc': 0.7551020408163265}, {'decision': 2, 'optimal_auc': 0.9727891156462585, 'imitation_auc': 0.7987921169739352, 'optimal_acc': 0.9727891156462585, 'imitation_acc': 0.8299319727891157}]
______epoch 44 _____
val reward 0.16575327515602112
imitation reward 1.8972368240356445
distributions [0.9883817434310913, 0.0005309924599714577, 0.019284134730696678]
[{'decision': 0, 'optimal_auc': 0.9795918367346939, 'imitation_auc': 0.5333969465648855, 'optimal_acc': 0.9795918367346939, 'imitation_acc': 0.8503401360544217}, {'decision': 1, 'optimal_auc': 1.0, 'imitation_auc

______epoch 58 _____
val reward 0.1788422018289566
imitation reward 2.2527809143066406
distributions [0.9895968437194824, 0.0006935135461390018, 0.017354972660541534]
[{'decision': 0, 'optimal_auc': 0.9795918367346939, 'imitation_auc': 0.5477099236641221, 'optimal_acc': 0.9795918367346939, 'imitation_acc': 0.8435374149659864}, {'decision': 1, 'optimal_auc': 1.0, 'imitation_auc': 0.6771739130434782, 'optimal_acc': 1.0, 'imitation_acc': 0.7619047619047619}, {'decision': 2, 'optimal_auc': 0.9727891156462585, 'imitation_auc': 0.7914812460267006, 'optimal_acc': 0.9727891156462585, 'imitation_acc': 0.8299319727891157}]
______epoch 59 _____
val reward 0.18092644214630127
imitation reward 2.260493278503418
distributions [0.9897916913032532, 0.000739537354093045, 0.017468998208642006]
[{'decision': 0, 'optimal_auc': 0.9795918367346939, 'imitation_auc': 0.5472328244274809, 'optimal_acc': 0.9795918367346939, 'imitation_acc': 0.8435374149659864}, {'decision': 1, 'optimal_auc': 1.0, 'imitation_auc'

In [ ]:
def torch_apply_along_axis(function, x, axis: int = 0):
    return torch.stack([
        function(x_i) for x_i in torch.unbind(x, dim=axis)
    ], dim=axis)

def get_unique_sequence(array):
    #converts a row of boolean values to a unique number e.g. [1,1,0] => 11, [0,0,1] => 100
    uniqueify = lambda r: torch.sum(torch.stack([i*(10**ii) for ii,i in enumerate(r)]))
    return torch_apply_along_axis(uniqueify,array)

def train_decision_model_triplet(
    tmodel1,
    tmodel2,
    tmodel3,
    use_default_split=True,
    use_bagging_split=False,
    lr=.0001,
    epochs=10000,
    patience=50,
    weights=[-1,1,1,-1], #realtive weight of survival, feeding tube, aspiration, andl lrc
    opt_weights=[1,1,1],
    imitation_weights=[.5,1,1],#weights of imitation decisions, because ic overtrains too quickly
    imitation_weight=1,
    reward_weight=1,
    imitation_triplet_weight=2,
    reward_triplet_weight = 2,
    shufflecol_chance = 0.1,
    split=.7,
    resample_training=False,
    save_path='../data/models/',
    file_suffix='',
    verbose=True,
    validate_with_memory=True,
    **model_kwargs,
):
    tmodel1.eval()
    tmodel2.eval()
    tmodel3.eval()

    train_ids, test_ids = get_tt_split(use_default_split=use_default_split,use_bagging_split=use_bagging_split,resample_training=resample_training)
    true_ids = train_ids + test_ids #for saving memory without upsampling

    dataset = DTDataset()
    data = dataset.processed_df.copy()
    
    def get_dlt(state):
        if state == 2:
            return data[Const.dlt2].copy()
        d = data[Const.dlt1].copy()
        if state < 1:
            d.values[:,:] = 0
        return d
    
    def get_pd(state):
        if state == 2:
            return data[Const.primary_disease_states2].copy()
        d = data[Const.primary_disease_states].copy()
        if state < 1:
            d.values[:,:] = 0
        return d
    
    def get_nd(state):
        if state == 2:
            return data[Const.nodal_disease_states2].copy()
        d = data[Const.nodal_disease_states].copy()
        if state < 1:
            d.values[:,:] = 0
        return d
    
    def get_cc(state):
        res = data[Const.ccs].copy()
        if state == 1:
            res.values[:,:] = np.zeros(res.values.shape)
        return res
    
    def get_mod(state):
        res = data[Const.modifications].copy()
        #this should have an ic condition but we don't use it anumore anywa
        return res
        
    outcomedf = data[Const.outcomes]
    baseline = dataset.get_state('baseline')
    
    def formatdf(d,dids=train_ids):
        d = df_to_torch(d.loc[dids]).to(model.get_device())
        return d
    
    def makegrad(v):
        if not v.requires_grad:
            v.requires_grad=True
        return v
    
    model = DecisionModel(baseline.shape[1],**model_kwargs)

    hashcode = str(hash(','.join([str(i) for i in train_ids])))
    
    save_file = save_path + 'model_' + model.identifier +'_hash' + hashcode + file_suffix + '.tar'
    model.fit_normalizer(df_to_torch(baseline.loc[train_ids]))
    optimizer = torch.optim.Adam(model.parameters(),lr=lr)
    
    
    optimal_train,transitions_train = calc_optimal_decisions(dataset,train_ids,tmodel1,tmodel2,tmodel3,
                                           weights=weights,
                                          )
    optimal_test,transitions_test = calc_optimal_decisions(dataset,test_ids,tmodel1,tmodel2,tmodel3,
                                          weights=weights,
                                         )
    optimal_train = optimal_train.to(model.get_device())
    optimal_test = optimal_test.to(model.get_device())
    mse = torch.nn.MSELoss()
    nllloss = torch.nn.NLLLoss()
    bce = torch.nn.BCELoss()
    
    def compare_decisions(d1,d2,d3,ids):
#         ypred = np.concatenate([dd.cpu().detach().numpy().reshape(-1,1) for dd in [d1,d2,d3]],axis=1)
        ytrue = df_to_torch(outcomedf.loc[ids])
        dloss = bce(d1.view(-1),ytrue[:,0])
        dloss += bce(d2.view(-1),ytrue[:,1])
        dloss += bce(d3,view(-1),ytrue[:,2])
        return dloss
        
    def remove_decisions(df):
        cols = [c for c in df.columns if c not in Const.decisions ]
        ddf = df[cols]
        return ddf
    
    makeinput = lambda step,dids: df_to_torch(remove_decisions(dataset.get_input_state(step=step,ids=dids)))
    threshold = lambda x: torch.gt(x,torch.rand(x.shape[0])).type(torch.FloatTensor)

    randchoice = lambda x: x[torch.randint(len(x),(1,))[0]]
    tloss_func = torch.nn.TripletMarginLoss()
    def get_tloss(row,step,yt,x,imitation=True):
        if yt[:,step].std() < .001:
            return torch.tensor([0])
        positive_idx= torch.nonzero(yt[:,step] == yt[row,step])
        positive_idx = torch.stack([ii for ii in positive_idx if ii != row]).view(-1)
        negative_idx = torch.tensor([ii for ii in range(x.shape[0]) if ii not in positive_idx and ii != row])
        if len(positive_idx) < 1 or len(negative_idx) < 1:
            print('no losses','n positive',len(positive_idx),'n negative',len(negative_idx),'yt',yt[row,step],'row',row,'step',step,'imitation',imitation,end='\r')
            return torch.tensor([0])
        positive = x[randchoice(positive_idx)]
        negative = x[randchoice(negative_idx)]
        anchor = x[row]
        [anchor_embedding,pos_embedding,neg_embedding] = [model.get_embedding(xx.view(1,-1),position=step,concatenate=False)[int(imitation)] for xx in [anchor,positive,negative]]
        tloss = tloss_func(anchor_embedding,pos_embedding,neg_embedding)
        return tloss
        
    def step(train=True):
        if train:
            model.train(True)
            tmodel1.train(True)
            tmodel2.train(True)
            tmodel3.train(True)
            optimizer.zero_grad()
            ids = train_ids
            y_opt = makegrad(optimal_train)
            transition_dict = {k: torch.clone(v).detach() for k,v in transitions_train.items()}
        else:
            ids = test_ids
            model.eval()
            tmodel1.eval()
            tmodel2.eval()
            tmodel3.eval()
            y_opt = makegrad(optimal_test)
            transition_dict = {k: torch.clone(v).detach() for k,v in transitions_test.items()}
            
        ytrain = df_to_torch(outcomedf.loc[ids])
        #imitation losses and decision 1
        xxtrained = [baseline, get_dlt(0),get_dlt(0),get_pd(0),get_nd(0),get_cc(0),get_mod(0)]
        xxtrain = [formatdf(xx,ids) for xx in xxtrained]
        xxtrain = torch.cat(xxtrain,axis=1)
        
        o1 = model(xxtrain,position=0)
        decision1_imitation = o1[:,3]
        decision1_opt = o1[:,0]
    
        imitation_loss1 = bce(decision1_imitation,ytrain[:,0])
        imitation_loss1 = torch.mul(imitation_loss1,imitation_weights[0])
        opt_loss1 = bce(decision1_opt,y_opt[:,0])
        opt_loss1 = torch.mul(opt_loss1,opt_weights[0])
        
        x1_imitation = [baseline, get_dlt(1),get_dlt(0),get_pd(1),get_nd(1),get_cc(1),get_mod(1)]
        x1_imitation = [formatdf(xx1,ids) for xx1 in x1_imitation]
        x1_imitation = torch.cat(x1_imitation,axis=1)
        
        o2 = model(x1_imitation,position=1)
            
        decision2_imitation = o2[:,4]
            
        imitation_loss2 =  bce(decision2_imitation,ytrain[:,1])
        imitation_loss2 = torch.mul(imitation_loss2,imitation_weights[1])
        
        
        x2_imitation = [baseline, get_dlt(1),get_dlt(2),get_pd(2),get_nd(2),get_cc(2),get_mod(2)]
        
        x2_imitation = [formatdf(xx2,ids) for xx2 in x2_imitation]
        x2_imitation = torch.cat(x2_imitation,axis=1)
        
        
        o3 = model(x2_imitation,position=2)
            
        decision3_imitation = o3[:,5]
        
        imitation_loss3 = bce(decision3_imitation,ytrain[:,2])
        imitation_loss3 = torch.mul(imitation_loss3,imitation_weights[2])
        
        opt_input2 = [
            formatdf(baseline,ids), 
            transition_dict['dlt1'],
            formatdf(get_dlt(0),ids),
            transition_dict['pd1'],
            transition_dict['nd1'], 
            formatdf(get_cc(0),ids),
            transition_dict['mod']
                 ]

        opt_input2 = torch.cat(opt_input2,axis=1)
        decision2_opt = model(opt_input2,position=1)[:,1]
        
        opt_loss2 = bce(decision2_opt,y_opt[:,1])
        opt_loss2 = torch.mul(opt_loss2,opt_weights[1])
        
        opt_input3 = [
            formatdf(baseline,ids),
            transition_dict['dlt1'],
            transition_dict['dlt2'],
            transition_dict['pd2'],
            transition_dict['nd2'],
            transition_dict['cc'],
            transition_dict['mod'],
        ]
        
        opt_input3 = torch.cat(opt_input3,axis=1)
        decision3_opt = model(opt_input3,position=2)[:,2]
        
        opt_loss3 = bce(decision3_opt,y_opt[:,2])
        opt_loss3 = torch.mul(opt_loss3,opt_weights[2])
        
        iloss = torch.add(torch.add(imitation_loss1,imitation_loss2),imitation_loss3)
        iloss = torch.mul(iloss,imitation_weight)
        
        reward_loss = torch.add(torch.add(opt_loss1,opt_loss2),opt_loss3)
        reward_loss =torch.mul(reward_loss,reward_weight)
        
        loss = torch.add(iloss,reward_loss)
        
        imitation_tloss = torch.FloatTensor([0])
        opt_tloss = torch.FloatTensor([0])
        n_rows = xxtrain.shape[0]
        if reward_triplet_weight + imitation_triplet_weight > 0.0001:
            for i in range(n_rows):
                if imitation_triplet_weight > .0001:
                    imitation_tloss += get_tloss(i,0,ytrain,xxtrain,True)
                    imitation_tloss += get_tloss(i,1,ytrain,x1_imitation,True)
                    imitation_tloss += get_tloss(i,2,ytrain,x2_imitation,True)
                if reward_triplet_weight > .0001:
                    opt_tloss += get_tloss(i,0,y_opt,xxtrain,False)
                    opt_tloss += get_tloss(i,1,y_opt,opt_input2,False)
                    opt_tloss += get_tloss(i,2,y_opt,opt_input3,False)
            loss += torch.mul(imitation_tloss[0],imitation_triplet_weight/n_rows)
            loss += torch.mul(opt_tloss[0],reward_triplet_weight/n_rows)
        losses = [iloss,reward_loss,imitation_tloss*imitation_triplet_weight/n_rows,opt_tloss*reward_triplet_weight/n_rows]
        
        if train:
            loss.backward()
            optimizer.step()
            return losses
        else:
            scores = []
            distributions = [decision1_opt.mean().item(),decision2_opt.mean().item(),decision3_opt.mean().item()]
            imitation = [decision1_imitation,decision2_imitation,decision3_imitation]
            optimal = [decision1_opt,decision2_opt,decision3_opt]
            for i,decision_im in enumerate(imitation):
                deci = decision_im.cpu().detach().numpy()
                deci0 = (deci > .5).astype(int)
                iout = ytrain[:,i].cpu().detach().numpy()
                acci = accuracy_score(iout,deci0)
                try:
                    auci = roc_auc_score(iout,deci)
                except:
                    auci = -1
                
                deco = optimal[i].cpu().detach().numpy()
                deci0 = (deco > .5).astype(int)
                oout = y_opt[:,i].cpu().detach().numpy()
                acco = accuracy_score(oout,deci0)
                try:
                    auco = roc_auc_score(oout,deco)
                except:
                    auco=-1
                scores.append({'decision': i,'optimal_auc': acco,'imitation_auc': auci,'optimal_acc': acco,'imitation_acc': acci})
            return losses, scores, distributions
        
    best_val_loss = torch.tensor(1000000000.0)
    steps_since_improvement = 0
    best_val_score = {}
    
    for epoch in range(epochs):
        losses = step(True)
        val_losses,val_metrics,val_distributions = step(False)
        vl = 0
        for vm in val_metrics:
            vl += -((vm['optimal_auc']*reward_weight) + (vm['imitation_auc']*imitation_weight))
        if verbose:
            print('______epoch',str(epoch),'_____')
            print('val reward',val_losses[1].item())
            print('imitation reward', val_losses[0].item())
            print('distance losses',val_losses[2].item(),val_losses[-1].item())
            print('distributions',val_distributions)
            print(val_metrics)
        if vl < best_val_loss:
            best_val_loss = vl
            best_val_score = val_metrics
            best_val_distributions = val_distributions
            steps_since_improvement = 0
            torch.save(model.state_dict(),save_file)
        else:
            steps_since_improvement += 1
        if steps_since_improvement > patience:
            break
    print('++++++++++Final+++++++++++')
    print('best',best_val_loss)
    print(best_val_score)
    model.load_state_dict(torch.load(save_file))
    model.eval()
    return model, best_val_score, best_val_loss, best_val_distributions

from Models import *
args = {
    'hidden_layers': [500], 
    'dropout': 0.75, 
    'input_dropout': 0.5, 
    'shufflecol_chance':  0.1,
    'opt_layer_size': 100,
    'imitation_layer_size': 100,
}

#1.8424
decision_model, decision_score, decision_loss, _ = train_decision_model_triplet(
    emodel1,emodel2,emodel3,
    lr=.001,
    imitation_weight=1,
    reward_weight=1,
    verbose=True,
    **args)
decision_model

______epoch 0 _____
val reward 1.9785244464874268
imitation reward 1.6434388160705566
distance losses 4.985600471496582 2.6588785648345947
distributions [0.5149250030517578, 0.4865598678588867, 0.4636133909225464]
[{'decision': 0, 'optimal_auc': 0.7142857142857143, 'imitation_auc': 0.5935114503816794, 'optimal_acc': 0.7142857142857143, 'imitation_acc': 0.6326530612244898}, {'decision': 1, 'optimal_auc': 0.7006802721088435, 'imitation_auc': 0.5230978260869565, 'optimal_acc': 0.7006802721088435, 'imitation_acc': 0.782312925170068}, {'decision': 2, 'optimal_auc': 0.9047619047619048, 'imitation_auc': 0.5785123966942148, 'optimal_acc': 0.9047619047619048, 'imitation_acc': 0.8299319727891157}]
______epoch 1 _____
val reward 1.8094353675842285
imitation reward 1.5871162414550781
distance losses 5.154726982116699 2.389582633972168
distributions [0.5420056581497192, 0.4425005316734314, 0.4294127821922302]
[{'decision': 0, 'optimal_auc': 0.891156462585034, 'imitation_auc': 0.571087786259542, 'op

______epoch 13 _____
val reward 0.8333570957183838
imitation reward 1.2387696504592896
distance losses 5.0655951499938965 2.0497779846191406
distributions [0.8024290800094604, 0.11773373186588287, 0.1518038809299469]
[{'decision': 0, 'optimal_auc': 0.891156462585034, 'imitation_auc': 0.36164122137404575, 'optimal_acc': 0.891156462585034, 'imitation_acc': 0.891156462585034}, {'decision': 1, 'optimal_auc': 1.0, 'imitation_auc': 0.5304347826086957, 'optimal_acc': 1.0, 'imitation_acc': 0.782312925170068}, {'decision': 2, 'optimal_auc': 0.9455782312925171, 'imitation_auc': 0.42466624284806104, 'optimal_acc': 0.9455782312925171, 'imitation_acc': 0.8231292517006803}]
______epoch 14 _____
val reward 0.8011651635169983
imitation reward 1.2278335094451904
distance losses 5.504003047943115 1.8861218690872192
distributions [0.8170573711395264, 0.10442814230918884, 0.13864853978157043]
[{'decision': 0, 'optimal_auc': 0.891156462585034, 'imitation_auc': 0.3649809160305343, 'optimal_acc': 0.891156462

______epoch 26 _____
val reward 0.5962144732475281
imitation reward 1.1153857707977295
distance losses 5.204978942871094 1.7045104503631592
distributions [0.8849633932113647, 0.034312210977077484, 0.0765872523188591]
[{'decision': 0, 'optimal_auc': 0.891156462585034, 'imitation_auc': 0.5271946564885497, 'optimal_acc': 0.891156462585034, 'imitation_acc': 0.891156462585034}, {'decision': 1, 'optimal_auc': 1.0, 'imitation_auc': 0.6959239130434782, 'optimal_acc': 1.0, 'imitation_acc': 0.782312925170068}, {'decision': 2, 'optimal_auc': 0.9455782312925171, 'imitation_auc': 0.6821360457724094, 'optimal_acc': 0.9455782312925171, 'imitation_acc': 0.8231292517006803}]
______epoch 27 _____
val reward 0.5840666890144348
imitation reward 1.108181118965149
distance losses 5.5994110107421875 1.4433095455169678
distributions [0.8837067484855652, 0.03250867500901222, 0.07642897218465805]
[{'decision': 0, 'optimal_auc': 0.891156462585034, 'imitation_auc': 0.5362595419847328, 'optimal_acc': 0.89115646258

______epoch 39 _____
val reward 0.47554463148117065
imitation reward 1.075225591659546
distance losses 5.422534942626953 1.4140580892562866
distributions [0.8552900552749634, 0.02145528979599476, 0.08373839408159256]
[{'decision': 0, 'optimal_auc': 0.891156462585034, 'imitation_auc': 0.5720419847328244, 'optimal_acc': 0.891156462585034, 'imitation_acc': 0.891156462585034}, {'decision': 1, 'optimal_auc': 1.0, 'imitation_auc': 0.7154891304347826, 'optimal_acc': 1.0, 'imitation_acc': 0.782312925170068}, {'decision': 2, 'optimal_auc': 0.9455782312925171, 'imitation_auc': 0.7523839796567069, 'optimal_acc': 0.9455782312925171, 'imitation_acc': 0.8095238095238095}]
______epoch 40 _____
val reward 0.46857666969299316
imitation reward 1.0748940706253052
distance losses 5.043469429016113 1.220170497894287
distributions [0.8541609048843384, 0.020873621106147766, 0.08364953100681305]
[{'decision': 0, 'optimal_auc': 0.891156462585034, 'imitation_auc': 0.5696564885496184, 'optimal_acc': 0.8911564625

In [ ]:
# for iteration in range(10):
#     tempmodel, tempscore,temploss,_ = train_decision_model(
#         emodel1,emodel2,emodel3,
#         lr=.001,
#         use_attention=True,
#         imitation_weight=1,
#         reward_weight=1,
#         validate_with_memory=True,
#         use_smote=False,
#         verbose=False,
#         threshold_decisions=False,
#         **args)
#     if temploss < decision_loss:
#         print('new best',tempscore)
#         print('vs',decision_score)
#         decision_model = tempmodel
#         decision_score = tempscore
#         decision_loss = temploss

In [ ]:
def gridsearch_triplet_model(m1,m2,m3,weights=[1,1,1,1]):
    hidden_layers = [[10],[50],[100],[200],[500],[1000]]
    extra_layers = [3,5,10,20,50,100,200]
    best_loss = 100000000000
    best_metrics = {}
    best_args = {}
    best_model = None
    best_record = {}
    k = 0
    records = []
    for hl in hidden_layers:
        for el in extra_layers:
            args = {'hidden_layers': hl, 'opt_layer_size': el, 'imitation_layer_size': el}
            for dropout in [.1,.25.5,.75]:
                args['dropout'] = dropout
                for input_dropout in [0.1,.25,.5]:
                    args['input_dropout'] = input_dropout
                    for shufflecol_chance in [.1,.5]:
                        try:
                            args['shufflecol_chance'] = shufflecol_chance
                            model,m_metrics,m_loss,m_distribution = train_decision_model_triplet(m1,m2,m3,
                                                                        lr=.001,
                                                                        weights=weights,
                                                                        verbose=False,
                                                                        **args)
                            entry = {
                                'metrics': m_metrics,
                                'loss': m_loss,
                                'args': args,
                                'distribution': m_distribution,
                                'smote': use_smote
                            }
                            records.append(entry)
                            print('done',k,m_loss)
                            print('curr best',best_loss)
                            k+=1
                            if m_loss < best_loss:
                                best_loss = m_loss
                                best_metrics  = m_metrics
                                best_model = model
                                best_args = args
                                best_record = entry
                                print('_++++++++++New Best++++____')
                                print(best_loss)
                                print(best_metrics)
                                print(best_args)
                                print('___________')
                                print('++++++++')
                                print()
                        except Exception as e:
                            print('error',e,args)
    print('_________')
    print('+++++++++++')
    print('best stuff',best_loss)
    print(best_metrics)
    print(best_args)
    return best_model, records, best_record

decision_model_best,records, bestr = gridsearch_triplet_model(emodel1,emodel2,emodel3,weights=[-1,1,1,-1])
records

In [ ]:
bestr

In [ ]:
# torch.save(model1,'../data/models/final_transition1_model_' + emodel1.identifier + '.pt')
# torch.save(model2,'../data/models/final_transition2_model_' + emodel2.identifier + '.pt')
# torch.save(model3,'../data/models/final_outcome_model_' + emodel3.identifier + '.pt')
# print('../data/models/final_transition1_model_' + emodel1.identifier + '.pt')
# print('../data/models/final_transition2_model_' + emodel2.identifier + '.pt')
# print('../data/models/final_outcome_model_' + emodel3.identifier + '.pt')

In [119]:
decision_model.set_device('cpu')
emodel1.set_device('cpu')
emodel2.set_device('cpu')
emodel3.set_device('cpu')
torch.save(decision_model,'../resources/decision_model.pt')
torch.save(emodel1,'../resources/transition1_model.pt')
torch.save(emodel2,'../resources/transition2_model.pt')
torch.save(emodel3,'../resources/outcome_model.pt')

PicklingError: Can't pickle <class 'Models.OutcomeSimulator'>: it's not the same object as Models.OutcomeSimulator

In [ ]:
def get_default_predictions(dm):
    res  = []
    for state in [0,1,2]:
        mem = dm.memory[state]
        mem = torch.median(mem,dim=0)[0].type(torch.FloatTensor)
        val = dm(mem.reshape(1,-1),position=state)
        res.append(val.cpu().detach().numpy())
    return np.stack(res)
get_default_predictions(decision_model)